## Requirements

In [2]:
!git clone https://github.com/IlyaGusev/purano
%cd purano
!pip install -r requirements.txt -q
!pip install --upgrade pytorch-lightning transformers razdel

Cloning into 'purano'...
remote: Enumerating objects: 1132, done.
remote: Counting objects: 100% (1/1), done.
remote: Total 1132 (delta 0), reused 1 (delta 0), pack-reused 1131
Receiving objects: 100% (1132/1132), 1.32 MiB | 13.65 MiB/s, done.
Resolving deltas: 100% (679/679), done.
/content/purano
     |████████████████████████████████| 20.1 MB 5.2 MB/s 
     |████████████████████████████████| 1.6 MB 50.0 MB/s 
     |████████████████████████████████| 316 kB 57.7 MB/s 
     |████████████████████████████████| 584 kB 55.5 MB/s 
     |████████████████████████████████| 125 kB 57.1 MB/s 
     |████████████████████████████████| 4.0 MB 53.9 MB/s 
     |████████████████████████████████| 592 kB 58.9 MB/s 
     |████████████████████████████████| 16.6 MB 26.2 MB/s 
     |████████████████████████████████| 68 kB 6.3 MB/s 
     |████████████████████████████████| 49 kB 5.0 MB/s 
     |████████████████████████████████| 55 kB 3.4 MB/s 
     |████████████████████████████████| 85 kB 3.6 MB/s 
     |█████

In [3]:
import json
import os
import random
import pickle
from collections import defaultdict, Counter
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import Dataset
from pytorch_lightning import LightningModule
from transformers import AutoModel, AdamW, AutoTokenizer
import torchvision
from torch.utils.tensorboard import SummaryWriter
from pytorch_lightning import Trainer
from pytorch_lightning.callbacks import EarlyStopping, ModelCheckpoint
from torch.utils.data import DataLoader, RandomSampler
from torch.nn.utils.rnn import pad_sequence, pack_padded_sequence, pad_packed_sequence
from tqdm import tqdm
from statistics import median, mean
from sklearn.cluster import AgglomerativeClustering
from torch.optim.lr_scheduler import ReduceLROnPlateau
from purano.clusterer.metrics import calc_metrics
from purano.io.markup_tsv import read_markup_tsv



INITIAL_MODEL = "IlyaGusev/news_tg_rubert"
TARGET_SIZE = 256
MAX_TOKENS = 250
BATCH_SIZE = 12
NUM_WORKERS = 2

In [3]:
!nvidia-smi

Sun May  8 02:16:48 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   51C    P0    29W / 250W |      0MiB / 16280MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

## Data loading

In [7]:
!wget -q https://www.dropbox.com/s/iauipxcpsuwjw6o/documents.tar.gz
!wget -q https://www.dropbox.com/s/8lu6dw8zcrn840j/ru_clustering_0525_urls.tsv
!wget -q https://www.dropbox.com/s/3yh5ii20ijfbtb6/ru_clustering_0527_urls_final.tsv
!wget -q https://raw.githubusercontent.com/dialogue-evaluation/Russian-News-Clustering-and-Headline-Generation/main/data/clustering/ru_clustering_0529_urls_final_v2.tsv
!tar -xzvf documents.tar.gz

train.jsonl
public.jsonl
private.jsonl


In [5]:
!wget -q https://www.dropbox.com/s/ykqk49a8avlmnaf/ru_all_split.tar.gz
!tar -xzvf ru_all_split.tar.gz

tar: Ignoring unknown extended header keyword 'LIBARCHIVE.creationtime'
tar: Ignoring unknown extended header keyword 'SCHILY.dev'
tar: Ignoring unknown extended header keyword 'SCHILY.ino'
tar: Ignoring unknown extended header keyword 'SCHILY.nlink'
ru_all_train.jsonl
tar: Ignoring unknown extended header keyword 'LIBARCHIVE.creationtime'
tar: Ignoring unknown extended header keyword 'SCHILY.dev'
tar: Ignoring unknown extended header keyword 'SCHILY.ino'
tar: Ignoring unknown extended header keyword 'SCHILY.nlink'
ru_all_val.jsonl
tar: Ignoring unknown extended header keyword 'LIBARCHIVE.creationtime'
tar: Ignoring unknown extended header keyword 'SCHILY.dev'
tar: Ignoring unknown extended header keyword 'SCHILY.ino'
tar: Ignoring unknown extended header keyword 'SCHILY.nlink'
ru_all_test.jsonl


In [ ]:
#Getting an extended news dataset

documents = dict()

for news in ['ru_all_train.jsonl', 'ru_all_val.jsonl', 'ru_all_test.jsonl']:
  with open(news, "r") as f:
    for line in f:
        record = json.loads(line)
        documents[record["url"]] = record

test = dict()
val_texts = []

for news in ['public.jsonl', 'private.jsonl']:
  with open(news, "r") as r:
    for line in r:
        record = json.loads(line)
        test[record["url"]] = record

print(f'Total number of news: {len(documents)}, number of test news {len(test)}')
documents = {k:v for k,v in documents.items() if k not in test}
print(f'Total train: {len(documents)}')

documents = list(documents.values())

Total number of news: 684685, number of test news 39176
Total train: 645915


In [ ]:
random.shuffle(documents)
border = int(len(documents) * 0.8)
full_train_records = documents[:border]
full_val_records = documents[border:]

with open('full_train_records', 'wb') as pickle_file:
    pickle.dump(full_train_records, pickle_file)

with open('full_val_records', 'wb') as pickle_file:
    pickle.dump(full_val_records, pickle_file)

In [ ]:
#Cheking the quality of split

public_set = []
with open("public.jsonl", "r") as r:
    for line in r:
        public_set.append(json.loads(line))

train = {}
for i in range(len(full_train_records)):
  train[full_train_records[i]['url']] = full_train_records[i]['text']
  
val = {}
for i in range(len(full_val_records)):
  val[full_val_records[i]['url']] = full_val_records[i]['text']

public = {}
for i in range(len(public_set)):
  public[public_set[i]['url']] = public_set[i]['text']

print(len(public.keys() & train.keys()))
print(len(public.keys() & val.keys()))

0
0


In [ ]:
def form_triplets(docs_filename, pairs_filename):
    documents = dict()
    with open(docs_filename, "r") as f:
        for line in f:
            record = json.loads(line)
            documents[record["url"]] = record
        
    positives = defaultdict(list)
    negatives = defaultdict(list)
    with open(pairs_filename, "r") as f:
        header = next(f)
        for line in f:
            first_url, second_url, label = line.strip().split("\t")
            if "OK" in label:
                positives[first_url].append(second_url)
                positives[second_url].append(first_url)
            else:
                negatives[first_url].append(second_url)
                negatives[second_url].append(first_url)

    urls = list(documents.keys())
    records = []
    for pivot_url, positive_urls in positives.items():
        negative_urls = []
        if pivot_url in negatives:
            negative_urls = negatives.pop(pivot_url)
        if negative_urls:
            for positive_url in positive_urls:
                for negative_url in negative_urls:
                    records.append((documents[pivot_url], documents[positive_url], documents[negative_url]))
    for pivot_url, negative_urls in negatives.items():
        for negative_url in negative_urls:
            records.append((documents[pivot_url], documents[pivot_url], documents[negative_url]))
    return records

triplets = form_triplets("train.jsonl", "ru_clustering_0525_urls.tsv")
random.shuffle(triplets)
border = int(len(triplets) * 0.8)
train_records = triplets[:border]
val_records = triplets[border:]


with open('train_records', 'wb') as pickle_file:
    pickle.dump(train_records, pickle_file)

with open('val_records', 'wb') as pickle_file:
    pickle.dump(val_records, pickle_file)

In [2]:
class NewsDataset(Dataset):
    def __init__(self, records, model_path, max_tokens, bert_embeds=None):
        self.tokenizer = AutoTokenizer.from_pretrained(
            model_path,
            do_lower_case=False,
            do_basic_tokenize=False,
            strip_accents=False
        )
        
        self.max_tokens = max_tokens
        self.records = records
        self.bert_embeds = bert_embeds
    
    def __len__(self):
        return len(self.records)
    
    def __getitem__(self, index):
        samples = self.records[index]
      
        if type(samples) is tuple:
            samples = [s["title"] + " [SEP] " + s["text"] for s in samples]
            samples = [self.tokenizer(
                s,
               add_special_tokens=True,
               max_length=self.max_tokens,
               padding='max_length',
               truncation=True,
               return_tensors='pt'
               ) for s in samples]
            samples = [{key: value.squeeze(0) for key, value in s.items()} for s in samples]
            
            if self.bert_embeds is not None:
                bert_embeds = self.bert_embeds[index]
                return samples[0], samples[1], samples[2], bert_embeds[0], bert_embeds[1], bert_embeds[2]
            return samples[0], samples[1], samples[2]

        else:
            samples = samples["title"] + " [SEP] " + samples["text"]
            samples = self.tokenizer(
                samples,
                add_special_tokens=True,
                max_length=self.max_tokens,
                padding='max_length',
                truncation=True,
                return_tensors='pt'
                ) 

           
            samples = {key: value.squeeze(0) for key, value in samples.items()}
            
            if self.bert_embeds is not None:
               bert_embeds = self.bert_embeds[index]
               return samples, bert_embeds
            return samples

In [8]:
def get_loaders( 
    train_records, 
    val_records, 
    tokenizer_model, 
    max_tokens, 
    batch_size, 
    num_workers=2,               
    train_bert_embeds=None, 
    val_bert_embeds=None, 
    val_batch_size=None, 
    ):

  train_data = NewsDataset(
      records=train_records, model_path=tokenizer_model, 
      max_tokens=max_tokens, bert_embeds=train_bert_embeds, 
      )
  train_sampler = RandomSampler(train_data)
  train_loader = DataLoader(
      train_data, batch_size=batch_size, 
      num_workers=num_workers, sampler=train_sampler,
      )
  if val_batch_size is None:
    val_batch_size = batch_size
  val_data = NewsDataset(
      records=val_records, model_path=tokenizer_model, 
      max_tokens=max_tokens, bert_embeds=val_bert_embeds, 
      )
  val_loader = DataLoader(
      val_data, batch_size=val_batch_size, 
      num_workers=num_workers, 
      )
  
  return train_loader, val_loader, train_data.tokenizer

In [41]:
initial_train_loader, initial_val_loader, initial_tokenizer = get_loaders(
                                       train_records, val_records, 
                                       INITIAL_MODEL, MAX_TOKENS, 
                                       BATCH_SIZE, NUM_WORKERS,
                                       )

# Getting embeds from finetuned model




In [25]:
class Embedder(nn.Module):
    def __init__(self, model_path, freeze_bert, layer_num):
        super().__init__()

        self.model = AutoModel.from_pretrained(model_path)
        self.model.trainable = not freeze_bert
        self.bert_dim = self.model.config.hidden_size
        self.layer_num = layer_num
    
    def forward(self, input_ids, attention_mask):
        output = self.model(
           input_ids,
           attention_mask=attention_mask,
           return_dict=True,
           output_hidden_states=True
        )
        layer_embeddings = output.hidden_states[self.layer_num]
        embeddings = self.aggregate(layer_embeddings, attention_mask)
        norm = embeddings.norm(p=2, dim=1, keepdim=True)
        embeddings = embeddings.div(norm)
        return embeddings
    
    def aggregate(self, layer_embeddings, mask):
        raise NotImplementedError()
        

class MeanEmbedder(Embedder):
    def __init__(self, model_path, freeze_bert, layer_num, hidden_dim, use_masking=True):
        super().__init__(model_path, freeze_bert, layer_num)

        self.token_mapping = nn.Linear(self.bert_dim, hidden_dim)
        self.use_masking = use_masking

    def aggregate(self, layer_embeddings, mask):
        embeddings = self.token_mapping(layer_embeddings)
        if self.use_masking:
            expanded_mask = mask.unsqueeze(-1).expand(embeddings.size()).float()
            sum_embeddings = torch.sum(embeddings * expanded_mask, 1)
            sum_mask = torch.clamp(expanded_mask.sum(1), min=1e-9)
            return sum_embeddings / sum_mask
        return torch.mean(embeddings, dim=1)


class ClusteringTripletModel(LightningModule):
    def __init__(self, model_path, num_training_steps=None,
                 hidden_dim=TARGET_SIZE, freeze_bert=False,
                 layer_num=-1, margin=0.5, lr=1e-5):
        super().__init__()

        self.embedder = MeanEmbedder(
            model_path,
            freeze_bert=freeze_bert,
            layer_num=layer_num,
            hidden_dim=hidden_dim
        )

        self.triplet_loss = nn.TripletMarginWithDistanceLoss(
            margin=margin,
            distance_function=nn.PairwiseDistance(p=2)
        )

        self.lr = lr
        self.num_training_steps = num_training_steps

    def forward(self, pivots, positives, negatives):
        pivot_embeddings = self.embedder(pivots["input_ids"], pivots["attention_mask"])
        positive_embeddings = self.embedder(positives["input_ids"], positives["attention_mask"])
        negative_embeddings = self.embedder(negatives["input_ids"], negatives["attention_mask"])
        loss = self.triplet_loss(pivot_embeddings, positive_embeddings, negative_embeddings)
        return loss

    def training_step(self, batch, batch_nb):
        train_loss = self(*batch)
        return train_loss

    def validation_step(self, batch, batch_nb):
        val_loss = self(*batch)
        self.log("val_loss", val_loss, prog_bar=True, logger=True)
        return val_loss

    def configure_optimizers(self):
        optimizer = AdamW(self.parameters(), lr=self.lr)
        return [optimizer]

In [5]:
EPOCHS = 10
ACCUMULATE_GRAD_BATCHES = 8
LOG_EVERY_N_STEPS = 10

In [ ]:
model = ClusteringTripletModel(INITIAL_MODEL)
early_stop_callback = EarlyStopping(
    monitor="val_loss",
    min_delta=0.0001,
    patience=3,
    verbose=True,
    mode="min" 
)

checkpoint = ModelCheckpoint(
    monitor='val_loss',
    dirpath='/content',
    filename='clustering_news_bert'
)


trainer = Trainer(
    gpus=1,
    accumulate_grad_batches=ACCUMULATE_GRAD_BATCHES,
    max_epochs=EPOCHS,
    callbacks=[early_stop_callback, checkpoint],
    log_every_n_steps=LOG_EVERY_N_STEPS
)


trainer.fit(model, initial_train_loader, initial_val_loader)

In [42]:
initial_model = ClusteringTripletModel.load_from_checkpoint(
    model_path = INITIAL_MODEL,
    checkpoint_path = '/content/clustering_news_bert.ckpt',
    )

embedder = initial_model.embedder.cuda()

Some weights of the model checkpoint at IlyaGusev/news_tg_rubert were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertModel were not initialized from the model checkpoint at IlyaGusev/news_tg_rubert and are newly initialized: ['bert.pooler.dense.bias', 'bert.pooler.dense.we

In [14]:
def gen_batch(records, batch_size):
    batch_start = 0
    while batch_start < len(records):
        batch_end = batch_start + batch_size
        batch = records[batch_start: batch_end]
        batch_start = batch_end
        yield batch

def records_to_embeds(
              records, model, tokenizer, 
              batch_size, max_tokens_count,
              print_mean_timing=False,
              ):
    current_index = 0
    try:
      embeddings = np.zeros((len(records), model.target_size))
    except:
      embeddings = np.zeros((len(records), 256))
 
    starter, ender = torch.cuda.Event(enable_timing=True), torch.cuda.Event(enable_timing=True)
    time = 0

    for batch in gen_batch(records, batch_size):
        samples = [r["title"] + " [SEP] " + r["text"] for r in batch]
        
        inputs = tokenizer(
              samples,
              add_special_tokens=True,
              max_length=max_tokens_count,
              padding='max_length',
              truncation=True,
              return_tensors='pt'
        )
           
        batch_input_ids = inputs["input_ids"].cuda()
        batch_mask = inputs["attention_mask"].cuda()
        
        with torch.no_grad():
            model.eval().cuda()
            starter.record()
            batch_embeddings = model(batch_input_ids, batch_mask)
            ender.record()
            torch.cuda.synchronize()
            curr_time = starter.elapsed_time(ender)
            batch_embeddings = batch_embeddings.cpu().numpy()
        embeddings[current_index:current_index+batch_size, :] = batch_embeddings
        current_index += batch_size
        time += curr_time

    
    if print_mean_timing is True:
      print('Mean inference time per embed: ', time/len(records), 'ms')
    return embeddings

In [24]:
def gen_bert_embeddings(records, model, 
                        tokenizer, 
                        batch_size,
                        max_tokens_count,
                        ):
  pivot = records_to_embeds([r[0] for r in records], embedder, 
                                           tokenizer, batch_size=8, 
                                           max_tokens_count=MAX_TOKENS,
                            )
  pos = records_to_embeds([r[1] for r in records], embedder, 
                                           tokenizer, batch_size=8, 
                                           max_tokens_count=MAX_TOKENS,
                           )
  neg = records_to_embeds([r[2] for r in records], embedder, 
                                           tokenizer, batch_size=8, 
                                           max_tokens_count=MAX_TOKENS,
                           )
  embeddings_ = np.append(pivot, pos, axis=1)
  embeddings_bert = np.append(embeddings_, neg, axis=1)
  embeddings_bert = embeddings_bert.reshape(-1, 3, TARGET_SIZE)
  return embeddings_bert

In [ ]:
val_embeddings_bert = gen_bert_embeddings(val_records, embedder, 
                                          initial_tokenizer, batch_size=8, 
                                          max_tokens_count=MAX_TOKENS)
train_embeddings_bert = gen_bert_embeddings(train_records, embedder, 
                                            initial_tokenizer, batch_size=8, 
                                            max_tokens_count=MAX_TOKENS)

In [ ]:
with open('train_embeddings_bert', 'wb') as pickle_file:
    pickle.dump(train_embeddings_bert, pickle_file)

with open('val_embeddings_bert', 'wb') as pickle_file:
    pickle.dump(val_embeddings_bert, pickle_file)

/content/drive/MyDrive/NewsBert


In [ ]:
single_full_train_embeddings_bert = records_to_embeds(full_train_records, embedder, 
                                            initial_tokenizer, batch_size=8, 
                                            max_tokens_count=MAX_TOKENS)

with open('single_full_train_embeddings_bert', 'wb') as pickle_file:
    pickle.dump(single_full_train_embeddings_bert, pickle_file)

In [ ]:
single_full_val_embeddings_bert = records_to_embeds(full_val_records, embedder, 
                                            initial_tokenizer, batch_size=8, 
                                            max_tokens_count=MAX_TOKENS)


with open('single_full_val_embeddings_bert', 'wb') as pickle_file:
    pickle.dump(single_full_val_embeddings_bert, pickle_file)

# Evaluation of initial model

In [ ]:
def get_quality(markup, embeds, records, dist_threshold, print_result=False):
    clustering_model = AgglomerativeClustering(
        n_clusters=None,
        distance_threshold=dist_threshold,
        linkage="average",
        affinity="cosine"
    )

    clustering_model.fit(embeds)
    labels = clustering_model.labels_
    
    idx2url = dict()
    url2record = dict()
    for i, record in enumerate(records):
        idx2url[i] = record["url"]
        url2record[record["url"]] = record

    url2label = dict()
    for i, label in enumerate(labels):
        url2label[idx2url[i]] = label
        
    metrics = calc_metrics(markup, url2record, url2label)[0]
    if print_result:
        print()
        print("Accuracy: {:.1f}".format(metrics["accuracy"] * 100.0))
        print("Positives Recall: {:.1f}".format(metrics["1"]["recall"] * 100.0))
        print("Positives Precision: {:.1f}".format(metrics["1"]["precision"] * 100.0))
        print("Positives F1: {:.1f}".format(metrics["1"]["f1-score"] * 100.0))
        print("Distance: ", dist_threshold)
        sizes = list(Counter(labels).values())
        print("Max cluster size: ", max(sizes))
        print("Median cluster size: ", median(sizes))
        print("Avg cluster size: {:.2f}".format(mean(sizes)))
        return
    return metrics["1"]["f1-score"]

In [43]:
public_markup = read_markup_tsv("ru_clustering_0527_urls_final.tsv")

public_embeddings = records_to_embeds(public_set, embedder, initial_tokenizer, 
                                      batch_size=8, max_tokens_count=MAX_TOKENS,
                                      print_mean_timing=True)

get_quality(public_markup, public_embeddings, public_set, 0.38, True)

Mean inference time per embed:  7.8254074972464265 ms

Accuracy: 95.0
Positives Recall: 95.0
Positives Precision: 94.1
Positives F1: 94.6
Distance:  0.38
Max cluster size:  255
Median cluster size:  2.0
Avg cluster size: 3.23


In [44]:
private_set = []
with open("private.jsonl", "r") as r:
    for line in r:
        private_set.append(json.loads(line))


private_markup = read_markup_tsv("ru_clustering_0529_urls_final_v2.tsv")

private_embeddings = records_to_embeds(private_set, embedder, initial_tokenizer, 
                                      batch_size=8, max_tokens_count=MAX_TOKENS,
                                      print_mean_timing=True)

get_quality(private_markup, private_embeddings, private_set, 0.38, True)

Mean inference time per embed:  7.825124706241143 ms

Accuracy: 94.9
Positives Recall: 95.7
Positives Precision: 93.4
Positives F1: 94.5
Distance:  0.38
Max cluster size:  202
Median cluster size:  1
Avg cluster size: 3.14


In [ ]:
with open('public_set', 'wb') as pickle_file:
    pickle.dump(public_set, pickle_file)

In [ ]:
with open('private_set', 'wb') as pickle_file:
    pickle.dump(private_set, pickle_file)

#Distillation - Search for Best Score



In [7]:
class DistillEmbedder(nn.Module):
  def __init__(self, vocab_size, 
               word_emb_dim=128, 
               rnn_hidden_dim=128,
               rnn_layers_count=2,
               target_size=TARGET_SIZE, 
               to_gru=False,
               attentive_aggregation=False,
               ):

        super().__init__()

        self.target_size = TARGET_SIZE
        self.embedding = nn.Embedding(vocab_size, word_emb_dim)
        self.attentive_aggregation = attentive_aggregation
        
        if not to_gru:
          self.rnn = nn.LSTM(
            word_emb_dim, 
            rnn_hidden_dim, 
            num_layers=rnn_layers_count,
            bidirectional=True, 
            batch_first=True,
            )
        
        else:
          self.rnn = nn.GRU(
            word_emb_dim, 
            rnn_hidden_dim, 
            num_layers=rnn_layers_count,
            bidirectional=True, 
            batch_first=True,
            )


        self.linear = nn.Linear(rnn_hidden_dim*2, target_size)

        if attentive_aggregation:
          self.softmax = nn.Softmax(dim=1)     
          self.attn = nn.Sequential(
                nn.Linear(rnn_hidden_dim*2, rnn_hidden_dim),
                nn.ReLU(),
                nn.Linear(rnn_hidden_dim, 1)
            )
        

  def avg_aggregate(self, rnn_output, mask):
        sum_embeddings = torch.sum(rnn_output, 1)
        expanded_mask = mask.unsqueeze(-1).expand(rnn_output.size()).float()
        sum_mask = torch.clamp(expanded_mask.sum(1), min=1e-9).cuda()
        return sum_embeddings / sum_mask 
          
  
  def attentive_aggregate(self, rnn_output, mask):
        weights = self.softmax(self.attn(rnn_output).squeeze(-1)) * mask.cuda()
        embeddings = weights.unsqueeze(1).bmm(rnn_output).squeeze(1) 
        return embeddings       


  def forward(self, x, mask):
        lens = torch.sum(mask.cpu(), 1)
        x = self.embedding(x)
        #pack_padded_sequence before feeding into rnn
        x = pack_padded_sequence(x, lens, enforce_sorted=False, batch_first=True)
        x, _ = self.rnn(x)
        #pad_packed_sequence on our packed rnn output
        x, _ = pad_packed_sequence(x, batch_first=True, total_length=MAX_TOKENS)
        if self.attentive_aggregation:
          x = self.attentive_aggregate(x, mask)
        else:
          x = self.avg_aggregate(x, mask)
        x = self.linear(x)
        return x

In [8]:
class DistillClusteringModel(nn.Module):
    def __init__(self, vocab_size=119547,  
                 word_emb_dim=128, 
                 rnn_hidden_dim=128,
                 rnn_layers_count=2,
                 target_size=TARGET_SIZE, 
                 lr=1e-3, 
                 to_gru=False,
                 attentive_aggregation=False,
                 evaluate_cos_similarity=True,
                 ):
      
        super().__init__()

        self.embedder = DistillEmbedder(vocab_size=vocab_size, 
                                        word_emb_dim=word_emb_dim, 
                                        rnn_hidden_dim=rnn_hidden_dim, 
                                        rnn_layers_count=rnn_layers_count,
                                        target_size=target_size,
                                        to_gru=to_gru,
                                        attentive_aggregation=attentive_aggregation,
                                        )

        self.evaluate_cos_similarity = evaluate_cos_similarity
        if evaluate_cos_similarity:
          self.cosine_similarity = torch.nn.functional.cosine_similarity
        else:
          self.mse = torch.nn.MSELoss()

        self.lr = lr

    def forward(self, news):
        embeddings = self.embedder(news["input_ids"].cuda(), news['attention_mask'].cuda())
        return embeddings

    def loss(self, embeds, bert_embeds):
        if self.evaluate_cos_similarity:
          similarity = self.cosine_similarity(embeds, bert_embeds)
          loss = torch.mean(torch.ones(len(similarity)).cuda() - similarity)
        else: 
          loss = self.mse(embeds.float(), bert_embeds.float())
        return loss

In [9]:
def epoch_train(model, data_loader, optimizer, scheduler):
    train_loss = 0
    model.cuda().train()
    for i, samples in enumerate(tqdm(data_loader, desc='Train')):
       model.zero_grad()
       
       bert_embeds = samples[1].cuda()
       embeds = model(samples[0])

       loss = model.loss(embeds, bert_embeds)
       loss.backward()
       optimizer.step()
       train_loss += float(loss)
    loss = train_loss / len(data_loader)
    scheduler.step(loss)
    print('Train_loss: ', loss)
    return loss


def epoch_val(model, data_loader):
    val_loss = 0
    with torch.no_grad():  
      model.cuda().eval()
      for i, samples in enumerate(tqdm(data_loader, desc='Val')):
        bert_embeds = samples[1].cuda()
        embeds = model(samples[0])

        loss = model.loss(embeds, bert_embeds)
        val_loss += float(loss)
    loss = val_loss / len(data_loader)
    print('Val_loss: ', loss)
    return loss


def train(model, train_data_loader,
          val_data_loader, num_train_epochs, 
          output_dir, optimizer=torch.optim.Adam, 
          patience=3, scheduler_patience=2, 
          ):
      optimizer = optimizer(model.parameters(), lr=model.lr)
      scheduler = ReduceLROnPlateau(optimizer, patience=scheduler_patience)
      writer = SummaryWriter(output_dir)
      best_val_loss = 100000
      best_count = 0
      for epoch in range(num_train_epochs):
          train_loss = epoch_train(model, train_data_loader, optimizer, scheduler)
          val_loss = epoch_val(model, val_data_loader)
          writer.add_scalar('Loss/train', train_loss, epoch)
          writer.add_scalar('Loss/val', val_loss, epoch)
          writer.add_scalar('Learning rate', scheduler._last_lr[0], epoch)
          best_count += 1
         
          if val_loss < best_val_loss:
              best_val_loss = val_loss
              best_count = 0
              torch.save(model.state_dict(), os.path.join(output_dir, f'best-distill-bert.pt'))
          
          if best_count == patience:
              torch.save(model.state_dict(), os.path.join(output_dir, 'last_epoch.pt'))
              writer.close()
              break

      writer.close()
      torch.save(model.state_dict(), os.path.join(output_dir, 'last_epoch.pt'))

In [10]:
BATCH_SIZE = 128


train_loader, val_loader, tokenizer = get_loaders(full_train_records, full_val_records, 
                                       INITIAL_MODEL, MAX_TOKENS, BATCH_SIZE,
                                       single_full_train_embeddings_bert,
                                       single_full_val_embeddings_bert,
                                       )

##LSTM (2 layers) - Cosine similarity - Avg aggregation

In [ ]:
lstm_distill_cos = DistillClusteringModel()

train(lstm_distill_cos, train_loader, val_loader, 
      60, '/content/cos/avg_lstm',
      )

In [104]:
lstm_distill_cos = DistillClusteringModel()

lstm_distill_cos.load_state_dict(
    torch.load('/content/cos/avg_lstm/best-distill-bert.pt'))

distill_embedder = lstm_distill_cos.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, 
                                              batch_size=8, max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.3029242417964328 ms

Accuracy: 94.1
Positives Recall: 95.2
Positives Precision: 92.3
Positives F1: 93.7
Distance:  0.38
Max cluster size:  309
Median cluster size:  2.0
Avg cluster size: 3.94


In [105]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.1816775513634203 ms

Accuracy: 93.8
Positives Recall: 95.5
Positives Precision: 91.4
Positives F1: 93.4
Distance:  0.38
Max cluster size:  175
Median cluster size:  2.0
Avg cluster size: 3.78


##GRU (2 layers) - Cosine similarity - Avg aggregation

In [ ]:
gru_distill_cos = DistillClusteringModel(to_gru=True)

train(gru_distill_cos, train_loader, val_loader, 
      60, '/content/cos/avg_gru',
      )

In [118]:
gru_distill_cos = DistillClusteringModel(to_gru=True)

gru_distill_cos.load_state_dict(
    torch.load('/content/cos/avg_gru/best-distill-bert.pt'))

distill_embedder = gru_distill_cos.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, 
                                              batch_size=8, max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.1764846629593002 ms

Accuracy: 94.1
Positives Recall: 94.9
Positives Precision: 92.6
Positives F1: 93.7
Distance:  0.38
Max cluster size:  299
Median cluster size:  2
Avg cluster size: 3.87


In [119]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.1773488510838601 ms

Accuracy: 93.5
Positives Recall: 95.1
Positives Precision: 91.2
Positives F1: 93.1
Distance:  0.38
Max cluster size:  168
Median cluster size:  2.0
Avg cluster size: 3.76


##GRU (1 recurrent layer) - Cosine similarity - Avg aggregation

In [ ]:
gru_1layer_distill_cos = DistillClusteringModel(to_gru=True, rnn_layers_count=1)

train(gru_1layer_distill_cos, train_loader, val_loader, 
      60, '/content/cos/avg_gru_1layer',
      )

In [120]:
gru_1layer_distill_cos = DistillClusteringModel(to_gru=True, rnn_layers_count=1)

gru_1layer_distill_cos.load_state_dict(
    torch.load('/content/cos/avg_gru_1layer/best-distill-bert.pt'))

distill_embedder = gru_1layer_distill_cos.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, 
                                              batch_size=8, max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.6425558774357298 ms

Accuracy: 93.7
Positives Recall: 93.8
Positives Precision: 92.7
Positives F1: 93.3
Distance:  0.38
Max cluster size:  267
Median cluster size:  2
Avg cluster size: 3.61


In [121]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.7492244192931659 ms

Accuracy: 93.2
Positives Recall: 93.9
Positives Precision: 91.5
Positives F1: 92.7
Distance:  0.38
Max cluster size:  162
Median cluster size:  1.0
Avg cluster size: 3.49


##LSTM (2 layers) - MSE - Avg aggregation

In [ ]:
lstm_distill_mse = DistillClusteringModel(evaluate_cos_similarity=False)

train(lstm_distill_mse, train_loader, val_loader, 
      60, '/content/mse/avg_lstm',
      )

Train: 100%|██████████| 4037/4037 [07:08<00:00,  9.42it/s]


Train_loss:  0.002570586533954467


Val: 100%|██████████| 1010/1010 [01:24<00:00, 11.99it/s]


Val_loss:  0.00202639509133054


Train: 100%|██████████| 4037/4037 [07:11<00:00,  9.35it/s]


...

Val_loss:  0.0008462945987138492


Train: 100%|██████████| 4037/4037 [07:08<00:00,  9.42it/s]


Train_loss:  0.0006320025869585198


Val: 100%|██████████| 1010/1010 [01:21<00:00, 12.41it/s]


Val_loss:  0.0008461135931170112


In [ ]:
lstm_distill_mse = DistillClusteringModel(evaluate_cos_similarity=False)

lstm_distill_mse.load_state_dict(
    torch.load('/content/mse/avg_lstm/best-distill-bert.pt'))

distill_embedder = lstm_distill_mse.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, 
                                              batch_size=8, max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

In [ ]:
lstm_distill_mse = DistillClusteringModel(evaluate_cos_similarity=False)

lstm_distill_mse.load_state_dict(
    torch.load('/content/mse/avg_lstm/best-distill-bert.pt'))

distill_embedder = lstm_distill_mse.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, 
                                              batch_size=8, max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.4233783412739576 ms

Accuracy: 94.0
Positives Recall: 95.2
Positives Precision: 92.0
Positives F1: 93.6
Distance:  0.38
Max cluster size:  273
Median cluster size:  2.0
Avg cluster size: 4.03


In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.5233920652296036 ms

Accuracy: 94.1
Positives Recall: 95.7
Positives Precision: 91.7
Positives F1: 93.7
Distance:  0.38
Max cluster size:  162
Median cluster size:  2
Avg cluster size: 3.88


##GRU (2 layers) - MSE - Avg aggregation

In [ ]:
gru_distill_mse = DistillClusteringModel(to_gru=True, evaluate_cos_similarity=False)

train(gru_distill_mse, train_loader, val_loader, 
      60, '/content/mse/avg_gru',
      )

In [128]:
gru_distill_mse = DistillClusteringModel(to_gru=True, evaluate_cos_similarity=False)

gru_distill_mse.load_state_dict(
    torch.load('/content/mse/avg_gru/best-distill-bert.pt'))

distill_embedder = gru_distill_mse.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, 
                                              batch_size=8, max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.1712667855371042 ms

Accuracy: 94.2
Positives Recall: 95.5
Positives Precision: 92.1
Positives F1: 93.8
Distance:  0.38
Max cluster size:  287
Median cluster size:  2
Avg cluster size: 4.30


In [129]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.24867987562834 ms

Accuracy: 93.7
Positives Recall: 96.0
Positives Precision: 90.7
Positives F1: 93.3
Distance:  0.38
Max cluster size:  186
Median cluster size:  2.0
Avg cluster size: 4.18


##LSTM (2 layers) - MSE - Attn aggregation

In [10]:
lstm_distill_mse_attn = DistillClusteringModel(attentive_aggregation=True)

train(lstm_distill_mse_attn, train_loader, val_loader, 
      60, '/content/mse/attn_lstm',
      )

Train: 100%|██████████| 4037/4037 [08:00<00:00,  8.40it/s]


Train_loss:  0.0820204289172091


Val: 100%|██████████| 1010/1010 [01:30<00:00, 11.18it/s]


Val_loss:  0.10997983059713477


Train: 100%|██████████| 4037/4037 [07:58<00:00,  8.44it/s]


...

Val_loss:  0.10898106478568795


Train: 100%|██████████| 4037/4037 [07:53<00:00,  8.52it/s]


Train_loss:  0.07358346994243228


Val: 100%|██████████| 1010/1010 [01:26<00:00, 11.70it/s]


Val_loss:  0.10884660462154934


In [11]:
lstm_distill_mse_attn = DistillClusteringModel(attentive_aggregation=True)

lstm_distill_mse_attn.load_state_dict(
    torch.load('/content/mse/attn_lstm/best-distill-bert.pt'))

distill_embedder = lstm_distill_mse_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, 
                                              batch_size=8, max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.0988437845649948 ms

Accuracy: 94.2
Positives Recall: 95.1
Positives Precision: 92.4
Positives F1: 93.8
Distance:  0.38
Max cluster size:  277
Median cluster size:  2.0
Avg cluster size: 3.98


In [12]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.0930923494675393 ms

Accuracy: 94.0
Positives Recall: 95.6
Positives Precision: 91.7
Positives F1: 93.6
Distance:  0.38
Max cluster size:  179
Median cluster size:  2.0
Avg cluster size: 3.85


##GRU (2 layers) - MSE - Attn aggregation

In [24]:
gru_distill_mse_attn = DistillClusteringModel(attentive_aggregation=True, to_gru=True)

train(gru_distill_mse_attn, train_loader, val_loader, 
      60, '/content/mse/attn_gru',
      )

Train: 100%|██████████| 4037/4037 [07:44<00:00,  8.68it/s]


Train_loss:  0.38346861638521096


Val: 100%|██████████| 1010/1010 [01:28<00:00, 11.40it/s]


Val_loss:  0.2718536614567818


Train: 100%|██████████| 4037/4037 [07:43<00:00,  8.71it/s]


...

Val_loss:  0.1131591580371787


Train: 100%|██████████| 4037/4037 [07:44<00:00,  8.69it/s]


Train_loss:  0.0760372601270945


Val: 100%|██████████| 1010/1010 [01:27<00:00, 11.60it/s]


Val_loss:  0.11301841844224975


In [39]:
gru_distill_mse_attn = DistillClusteringModel(attentive_aggregation=True, to_gru=True)

gru_distill_mse_attn.load_state_dict(
    torch.load('/content/mse/attn_gru/best-distill-bert.pt'))

distill_embedder = gru_distill_mse_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, 
                                              batch_size=8, max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.53960982314144 ms

Accuracy: 94.3
Positives Recall: 95.1
Positives Precision: 92.8
Positives F1: 93.9
Distance:  0.38
Max cluster size:  279
Median cluster size:  2
Avg cluster size: 3.93


In [40]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.5448059391466005 ms

Accuracy: 94.1
Positives Recall: 95.3
Positives Precision: 92.0
Positives F1: 93.7
Distance:  0.38
Max cluster size:  174
Median cluster size:  2
Avg cluster size: 3.81


##GRU (2 layers) - MSE - Attn aggregation - Token embedding dimension 64

In [ ]:
gru_distill_mse_attn = DistillClusteringModel(attentive_aggregation=True, to_gru=True, word_emb_dim=64)

train(gru_distill_mse_attn, train_loader, val_loader, 
      60, '/content/mse/attn_gru/64emb',
      )

In [52]:
gru_distill_mse_attn = DistillClusteringModel(attentive_aggregation=True, to_gru=True, word_emb_dim=64)

gru_distill_mse_attn.load_state_dict(
    torch.load('/content/mse/attn_gru/64emb/best-distill-bert.pt'))

distill_embedder = gru_distill_mse_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, 
                                              batch_size=8, max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.5217533059804087 ms

Accuracy: 93.9
Positives Recall: 94.4
Positives Precision: 92.6
Positives F1: 93.5
Distance:  0.38
Max cluster size:  284
Median cluster size:  2
Avg cluster size: 4.01


In [53]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.5344844116143816 ms

Accuracy: 93.9
Positives Recall: 95.2
Positives Precision: 91.8
Positives F1: 93.5
Distance:  0.38
Max cluster size:  177
Median cluster size:  2
Avg cluster size: 3.86


#Error analysis

In [11]:
def get_errors(markup, embeds, records, dist_threshold):
    clustering_model = AgglomerativeClustering(
        n_clusters=None,
        distance_threshold=dist_threshold,
        linkage="average",
        affinity="cosine"
    )

    clustering_model.fit(embeds)
    labels = clustering_model.labels_
    
    idx2url = dict()
    url2record = dict()
    for i, record in enumerate(records):
        idx2url[i] = record["url"]
        url2record[record["url"]] = record

    url2label = dict()
    for i, label in enumerate(labels):
        url2label[idx2url[i]] = label
        
    errors = calc_metrics(markup, url2record, url2label)[1]
    return errors

In [13]:
gru_distill_mse_attn = DistillClusteringModel(attentive_aggregation=True, to_gru=True)

gru_distill_mse_attn.load_state_dict(
    torch.load('/content/mse/attn_gru/best-distill-bert.pt'))

distill_embedder = gru_distill_mse_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, 
                                              batch_size=8, max_tokens_count=MAX_TOKENS, 
                                              )
errors = get_errors(public_markup, public_distill_embeddings, public_set, 0.38)

In [14]:
errors

[{'first_text': 'Инцидентом заинтересовалась прокуратура. \n       В Московском районе Петербурга днем 27-го мая сгорел гараж. Об этом сообщила пресс-служба ГУ МЧС по Петербургу.  Инцидент произошел на проспекте Космонавтов, 106. Сообщение о пожаре поступило в 13:35. Как стало известно, там полностью выгорел неэксплуатируемый гараж и частично обгорел еще один гараж, который также не используется. В 13:57 пожар ликвидировали. Сведений о пострадавших уточняются.  После происшествия прокуратура организовала проверку. В ведомстве намерены дать оценку ситуации, установить лиц, которые причастны к ситуации, а также установить правомерность нахождения на территории.  Сейчас на участке идет строительство жилого комплекса. Ранее в Сестрорецке  сгорел  нежилой частный дом.  Видео: "ДТП и ЧП Санкт-Петербург"',
  'first_title': 'Видео: на Космонавтов загорелись несколько гаражей',
  'first_url': 'https://piter.tv/event/pozhar_na_Kosmonavtov/',
  'prediction': 1,
  'second_text': 'Огонь полностью у

In [17]:
import pandas as pd
errors_128 = pd.DataFrame(errors)
errors_128.to_csv('/content/mse/attn_gru/errors.csv')

In [18]:
gru_distill_mse_attn = DistillClusteringModel(attentive_aggregation=True, to_gru=True, word_emb_dim=64)

gru_distill_mse_attn.load_state_dict(
    torch.load('/content/mse/attn_gru/64emb/best-distill-bert.pt'))

distill_embedder = gru_distill_mse_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, 
                                              batch_size=8, max_tokens_count=MAX_TOKENS, 
                                              )
errors = get_errors(public_markup, public_distill_embeddings, public_set, 0.38)

In [19]:
errors

[{'first_text': 'Инцидентом заинтересовалась прокуратура. \n       В Московском районе Петербурга днем 27-го мая сгорел гараж. Об этом сообщила пресс-служба ГУ МЧС по Петербургу.  Инцидент произошел на проспекте Космонавтов, 106. Сообщение о пожаре поступило в 13:35. Как стало известно, там полностью выгорел неэксплуатируемый гараж и частично обгорел еще один гараж, который также не используется. В 13:57 пожар ликвидировали. Сведений о пострадавших уточняются.  После происшествия прокуратура организовала проверку. В ведомстве намерены дать оценку ситуации, установить лиц, которые причастны к ситуации, а также установить правомерность нахождения на территории.  Сейчас на участке идет строительство жилого комплекса. Ранее в Сестрорецке  сгорел  нежилой частный дом.  Видео: "ДТП и ЧП Санкт-Петербург"',
  'first_title': 'Видео: на Космонавтов загорелись несколько гаражей',
  'first_url': 'https://piter.tv/event/pozhar_na_Kosmonavtov/',
  'prediction': 1,
  'second_text': 'Огонь полностью у

In [20]:
errors_64 = pd.DataFrame(errors)
errors_64.to_csv('/content/mse/attn_gru/64emb/errors64.csv')

#Distillation Experiments

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


##Train cycle

In [45]:
def epoch_train(model, data_loader, optimizer):
    train_loss = 0
    model.cuda().train()
    for i, samples in enumerate(tqdm(data_loader, desc='Train')):
       model.zero_grad()
       if len(samples) == 6:
          bert_embeds = [samples[3].cuda(), samples[4].cuda(), samples[5].cuda()]
          embeds = model(samples[0], samples[1], samples[2])

       else:
          bert_embeds = samples[1].cuda()
          embeds = model(samples[0])

       loss = model.loss(embeds, bert_embeds)
      
       loss.backward()
       optimizer.step()
       train_loss += float(loss)
    loss = train_loss / len(data_loader)
    print('Train_loss: ', loss)
    return loss


def epoch_val(model, data_loader):
    val_loss = 0
    with torch.no_grad():  
      model.cuda().eval()
      for i, samples in enumerate(tqdm(data_loader, desc='Val')):
        if len(samples) == 6:
            bert_embeds = [samples[3].cuda(), samples[4].cuda(), samples[5].cuda()]
            embeds = model(samples[0], samples[1], samples[2])

        else:
            bert_embeds = samples[1].cuda()
            embeds = model(samples[0])

        loss = model.loss(embeds, bert_embeds)
        val_loss += float(loss)
    loss = val_loss / len(data_loader)
    print('Val_loss: ', loss)
    return loss



def train(model, train_data_loader, 
          val_data_loader, num_train_epochs, 
          output_dir, early_stopping = False, 
          patience=2, 
          optimizer=torch.optim.Adam, 
          ):
      optimizer = optimizer(model.parameters(), lr=model.lr) 
      writer = SummaryWriter(output_dir)
      best_val_loss = 100000
      best_count = 0
      for epoch in range(num_train_epochs):
          train_loss = epoch_train(model, train_data_loader, optimizer)
          val_loss = epoch_val(model, val_data_loader)
          writer.add_scalar('Loss/train', train_loss, epoch)
          writer.add_scalar('Loss/val', val_loss, epoch)
           
          best_count += 1
         
          if val_loss < best_val_loss:
              best_val_loss = val_loss
              best_count = 0
              torch.save(model.state_dict(), os.path.join(output_dir, f'best-distill-bert.pt'))
          
          if early_stopping:
            if best_count == patience:
              torch.save(model.state_dict(), os.path.join(output_dir, 'last_epoch.pt'))
              writer.close()
              break

      writer.close()
      torch.save(model.state_dict(), os.path.join(output_dir, 'last_epoch.pt'))

##--LSTM--

Distillation experiments based on LSTM architecture.

##Constructing Embedder model

In [7]:
class LSTM_Embedder(nn.Module):
  def __init__(self, vocab_size, target_size=TARGET_SIZE, 
               bidirectional=False, pretrained=False, 
               word_emb_dim=128, pretrained_embs=None, 
               rnn_hidden_dim=512, rnn_layers_count=1, 
               freeze_pretrained=False, add_relu=False, 
               del_linear=False, del_2_linear=False, 
               to_rnn=False, to_gru=False, 
               dropout=0.3, attentive_aggregation=False, 
               ):

        super().__init__()

        self.target_size = target_size
        self.del_linear = del_linear
        self.del_2_linear = del_2_linear
        self.add_relu = add_relu
        self.attentive_aggregation = attentive_aggregation

       
        if bidirectional:
          rnn_out_dim = 2*rnn_hidden_dim
        else:
          rnn_out_dim = rnn_hidden_dim

        if pretrained:
          self.embedding = nn.Embedding.from_pretrained(pretrained_embs, 
                                                        freeze=freeze_pretrained) 
          word_emb_dim = pretrained_embs.shape[1]
        else:
          self.embedding = nn.Embedding(vocab_size, word_emb_dim)

        if attentive_aggregation:
          self.softmax = nn.Softmax(dim=1)     
          self.attn = nn.Sequential(
                nn.Linear(rnn_out_dim, rnn_out_dim//2),
                nn.ReLU(),
                nn.Linear(rnn_out_dim//2, 1)
            )
        
        if to_rnn:
          self.rnn = nn.RNN(
            word_emb_dim, 
            rnn_hidden_dim, 
            num_layers=rnn_layers_count,
            bidirectional=bidirectional,
            batch_first=True,
            )
          
        elif to_gru:
          self.rnn = nn.GRU(
            word_emb_dim, 
            rnn_hidden_dim, 
            num_layers=rnn_layers_count,
            bidirectional=bidirectional,
            batch_first=True,
            )

        else:
          self.rnn = nn.LSTM(
            word_emb_dim, 
            rnn_hidden_dim, 
            num_layers=rnn_layers_count,
            bidirectional=bidirectional,
            batch_first=True,
            )
          
        
        self.dropout = nn.Dropout(dropout)
        self.model = nn.ModuleList([
          self.embedding,
          self.rnn,
          self.dropout,
          nn.Linear(rnn_out_dim, target_size),
          nn.Linear(target_size, target_size)])
        
        if self.del_linear:
          del self.model[3]
          self.model[3] = nn.Linear(rnn_out_dim, target_size)

        if self.del_2_linear:
          del self.model[3:]
        
  def aggregate(self, rnn_output, mask):
        expanded_mask = mask.unsqueeze(-1).expand(rnn_output.size()).float()
        sum_embeddings = torch.sum(rnn_output, 1)
        sum_mask = torch.clamp(expanded_mask.sum(1), min=1e-9).cuda()
        return sum_embeddings / sum_mask  

  def attentive_aggregate(self, rnn_output, mask):
        weights = self.softmax(self.attn(rnn_output).squeeze(-1)) * mask
        embeddings = weights.unsqueeze(1).bmm(rnn_output).squeeze(1)
        return embeddings

  def forward(self, x, mask):
        lens = torch.sum(mask.cpu(), 1)
        for i, layer in enumerate(self.model):
          if layer == self.rnn:
            #pack_padded_sequence before feeding into RNN
            x = pack_padded_sequence(x, lens, enforce_sorted=False, batch_first=True)
            x, _ = layer(x)
            #pad_packed_sequence on our packed RNN output
            x, _ = pad_packed_sequence(x, batch_first=True, total_length=MAX_TOKENS)
            #taking single output from the end of sequence
            if self.attentive_aggregation:
              x = self.attentive_aggregate(x, mask)
            else:
              x = self.aggregate(x, mask)
          elif self.add_relu and not self.del_linear and i==3:
            x = nn.functional.relu(layer(x))
          else:
            x = layer(x)

        return x

###Triplet + MSE (complex) loss Distillation

The main idea of the first experiments is to use for optimization both original Triplet loss and MSE loss between aggregated embeds. 

####Modeling and Preprocessing

In [7]:
%cd /content/drive/MyDrive/NewsBert
from initial_finetuned_model import ClusteringTripletModel
from loading_and_evaluation import gen_batch, records_to_embeds, get_quality, NewsDataset, get_loaders


with open('train_embeddings_bert', 'rb') as pickle_file:
    train_embeddings_bert = pickle.load(pickle_file)

with open('val_embeddings_bert', 'rb') as pickle_file:
    val_embeddings_bert = pickle.load(pickle_file)


with open('train_records', 'rb') as pickle_file:
    train_records = pickle.load(pickle_file)

with open('val_records', 'rb') as pickle_file:
    val_records = pickle.load(pickle_file)


with open('public_set', 'rb') as pickle_file:
    public_set = pickle.load(pickle_file)

with open('private_set', 'rb') as pickle_file:
    private_set = pickle.load(pickle_file)




initial_model = ClusteringTripletModel.load_from_checkpoint(
    model_path = INITIAL_MODEL,
    checkpoint_path = '/content/drive/MyDrive/NewsBert/best_clustering_news_bert-val_loss=0.0008.ckpt',
    num_training_steps = None
    )

embedder = initial_model.embedder.cuda()

VOCAB_SIZE = embedder.model.embeddings.word_embeddings.num_embeddings
BATCH_SIZE = 32

public_markup = read_markup_tsv("ru_clustering_0527_urls_final.tsv")
private_markup = read_markup_tsv("ru_clustering_0529_urls_final_v2.tsv")

/content/drive/MyDrive/NewsBert


Some weights of the model checkpoint at IlyaGusev/news_tg_rubert were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertModel were not initialized from the model checkpoint at IlyaGusev/news_tg_rubert and are newly initialized: ['bert.pooler.dense.bias', 'bert.pooler.dense.we

In [8]:
class ClusteringDistillModel(nn.Module):
    def __init__(self, vocab_size, target_size=TARGET_SIZE, 
                 bidirectional=False, pretrained=False, 
                 word_emb_dim=128, pretrained_embs=None, 
                 freeze_pretrained = False, 
                 rnn_hidden_dim=128, rnn_layers_count=1, 
                 dropout=0.3, margin=0.5, lr=1e-4, 
                 loss_alpha=0.5, add_relu=False,
                 del_linear=False, to_rnn=False,
                 to_gru=False,
                 del_2_linear=False,
                 attentive_aggregation=False,):
      
        super().__init__()

        self.embedder = LSTM_Embedder(vocab_size=vocab_size, 
                                      target_size=target_size, 
                                      bidirectional=bidirectional, 
                                      word_emb_dim=word_emb_dim, 
                                      rnn_hidden_dim=rnn_hidden_dim, 
                                      rnn_layers_count=rnn_layers_count, 
                                      pretrained=pretrained, 
                                      pretrained_embs=pretrained_embs, 
                                      freeze_pretrained=freeze_pretrained,
                                      dropout=dropout, add_relu=add_relu,
                                      del_linear=del_linear, to_rnn=to_rnn,
                                      to_gru=to_gru,
                                      del_2_linear=del_2_linear,
                                      attentive_aggregation=attentive_aggregation,
                                      )

        self.triplet_loss = nn.TripletMarginWithDistanceLoss(
            margin=margin,
            distance_function=nn.PairwiseDistance(p=2)
        )

        self.mse = torch.nn.MSELoss()
        self.lr = lr
        self.loss_alpha = loss_alpha

    def forward(self, pivots, positives, negatives):
        pivot_embeddings = self.embedder(pivots["input_ids"].cuda(), pivots["attention_mask"])
        positive_embeddings = self.embedder(positives["input_ids"].cuda(), positives["attention_mask"])
        negative_embeddings = self.embedder(negatives["input_ids"].cuda(), negatives["attention_mask"])
        return pivot_embeddings, positive_embeddings, negative_embeddings

    def loss(self, embeds, bert_embeds):
        anchor, positive, negative = embeds
        triplet_loss = self.triplet_loss(anchor, positive, negative) 
        distill_loss = torch.mean(torch.tensor([self.mse(embed, bert_embed) 
                          for embed, bert_embed in zip(embeds, bert_embeds)]))
        loss = self.loss_alpha*triplet_loss + (1-self.loss_alpha)*distill_loss
        return loss

In [9]:
train_loader_triplets, val_loader_triplets, tokenizer_triplets = get_loaders(
                                       train_records, val_records, 
                                       INITIAL_MODEL, MAX_TOKENS, 
                                       BATCH_SIZE, train_embeddings_bert,
                                       val_embeddings_bert,
                                       )

####Experiments: Simple LSTM

In [32]:
#Balancing loss_alpha
#Loss_alpha = 0.5

lstm_distill = ClusteringDistillModel(vocab_size = VOCAB_SIZE,)
train(lstm_distill, train_loader_triplets, val_loader_triplets, 
      100, '/content/drive/MyDrive/NewsBert/Distillation_Triplet_MSE/LSTM',
      True
      )

Train: 100%|██████████| 471/471 [00:51<00:00,  9.10it/s]


Train_loss:  0.1503095451023745


Val: 100%|██████████| 118/118 [00:10<00:00, 11.65it/s]


Val_loss:  0.09885545191013893


Train: 100%|██████████| 471/471 [00:41<00:00, 11.23it/s]


...

Val_loss:  0.053586144850901164


Train: 100%|██████████| 471/471 [00:39<00:00, 12.01it/s]


Train_loss:  0.024115286718523383


Val: 100%|██████████| 118/118 [00:09<00:00, 13.09it/s]


Val_loss:  0.05488807492431513


In [33]:
lstm_distill = ClusteringDistillModel(vocab_size = VOCAB_SIZE)

lstm_distill.load_state_dict(torch.load('/content/drive/MyDrive/NewsBert/Distillation_Triplet_MSE/LSTM/best-distill-bert.pt'))
distill_embedder = lstm_distill.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, 
                                              tokenizer_triplets, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)


Accuracy: 59.3
Positives Recall: 29.5
Positives Precision: 62.5
Positives F1: 40.1
Distance:  0.38
Max cluster size:  4238
Median cluster size:  852
Avg cluster size: 1181.18


In [34]:
lstm_distill = ClusteringDistillModel(vocab_size = VOCAB_SIZE)

lstm_distill.load_state_dict(torch.load('/content/drive/MyDrive/NewsBert/Distillation_Triplet_MSE/LSTM/best-distill-bert.pt'))
distill_embedder = lstm_distill.embedder.cuda()

private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.557725570331221 ms

Accuracy: 58.2
Positives Recall: 29.1
Positives Precision: 59.1
Positives F1: 39.0
Distance:  0.38
Max cluster size:  3606
Median cluster size:  340.0
Avg cluster size: 1060.89


In [35]:
#Loss_alpha = 0.2

lstm_distill = ClusteringDistillModel(vocab_size = VOCAB_SIZE, loss_alpha=0.2)
train(lstm_distill, train_loader_triplets, val_loader_triplets, 
      100, '/content/drive/MyDrive/NewsBert/Distillation_Triplet_MSE/LSTM/alpha02',
      True
      )

Train: 100%|██████████| 471/471 [00:39<00:00, 11.88it/s]


Train_loss:  0.06694279977935129


Val: 100%|██████████| 118/118 [00:09<00:00, 13.01it/s]


Val_loss:  0.04583849195074617


Train: 100%|██████████| 471/471 [00:39<00:00, 11.87it/s]


...

Val_loss:  0.03298407479448681


Train: 100%|██████████| 471/471 [00:39<00:00, 11.90it/s]


Train_loss:  0.02581546513365162


Val: 100%|██████████| 118/118 [00:08<00:00, 13.26it/s]


Val_loss:  0.03440205811582432


In [36]:
lstm_distill.load_state_dict(torch.load('/content/drive/MyDrive/NewsBert/Distillation_Triplet_MSE/LSTM/alpha02/best-distill-bert.pt'))
distill_embedder = lstm_distill.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, 
                                              tokenizer_triplets, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)


Accuracy: 59.8
Positives Recall: 25.7
Positives Precision: 66.6
Positives F1: 37.0
Distance:  0.38
Max cluster size:  2896
Median cluster size:  487
Avg cluster size: 803.20


In [37]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.568876001642097 ms

Accuracy: 58.3
Positives Recall: 22.7
Positives Precision: 62.8
Positives F1: 33.4
Distance:  0.38
Max cluster size:  2234
Median cluster size:  669.0
Avg cluster size: 795.67


In [38]:
#Loss_alpha = 1

lstm_distill = ClusteringDistillModel(vocab_size = VOCAB_SIZE, loss_alpha=1)
train(lstm_distill, train_loader_triplets, val_loader_triplets,
      100, '/content/drive/MyDrive/NewsBert/Distillation_Triplet_MSE/LSTM/alpha1',
      True
      )

Train: 100%|██████████| 471/471 [00:39<00:00, 11.95it/s]


Train_loss:  0.298526287142132


Val: 100%|██████████| 118/118 [00:08<00:00, 13.34it/s]


Val_loss:  0.18547999025401424


Train: 100%|██████████| 471/471 [00:39<00:00, 11.93it/s]


...

Val_loss:  0.07487122484056627


Train: 100%|██████████| 471/471 [00:38<00:00, 12.15it/s]


Train_loss:  0.004572053354889977


Val: 100%|██████████| 118/118 [00:08<00:00, 13.37it/s]


Val_loss:  0.07306267103275


In [39]:
lstm_distill.load_state_dict(torch.load('/content/drive/MyDrive/NewsBert/Distillation_Triplet_MSE/LSTM/alpha1/best-distill-bert.pt'))
distill_embedder = lstm_distill.embedder.cuda()

public_distill_embeddings = records_to_embeds(public_set, distill_embedder, 
                                              tokenizer_triplets, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,
                                              )
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)


Accuracy: 59.7
Positives Recall: 27.5
Positives Precision: 64.8
Positives F1: 38.6
Distance:  0.38
Max cluster size:  2639
Median cluster size:  1174.0
Avg cluster size: 1004.00


In [40]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.5646069075679699 ms

Accuracy: 59.0
Positives Recall: 23.7
Positives Precision: 64.9
Positives F1: 34.7
Distance:  0.38
Max cluster size:  2555
Median cluster size:  1086
Avg cluster size: 830.26


In [41]:
#Loss_alpha = 0

lstm_distill = ClusteringDistillModel(vocab_size = VOCAB_SIZE, loss_alpha=0)
train(lstm_distill, train_loader_triplets, val_loader_triplets,
      100, '/content/drive/MyDrive/NewsBert/Distillation_Triplet_MSE/LSTM/alpha0',
      True)

Train: 100%|██████████| 471/471 [00:38<00:00, 12.18it/s]


Train_loss:  0.006398983694228383


Val: 100%|██████████| 118/118 [00:08<00:00, 13.68it/s]


Val_loss:  0.0063250847722447785


Train: 100%|██████████| 471/471 [00:38<00:00, 12.24it/s]


...

Val_loss:  0.0063250847722447785


Train: 100%|██████████| 471/471 [00:38<00:00, 12.25it/s]


Train_loss:  0.006398701816241324


Val: 100%|██████████| 118/118 [00:08<00:00, 13.80it/s]


Val_loss:  0.0063250847722447785


In [42]:
lstm_distill.load_state_dict(torch.load('/content/drive/MyDrive/NewsBert/Distillation_Triplet_MSE/LSTM/alpha0/best-distill-bert.pt'))
distill_embedder = lstm_distill.embedder.cuda()

public_distill_embeddings = records_to_embeds(public_set, distill_embedder, 
                                              tokenizer_triplets, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,
                                              )
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)


Accuracy: 46.1
Positives Recall: 100.0
Positives Precision: 46.1
Positives F1: 63.1
Distance:  0.38
Max cluster size:  20080
Median cluster size:  20080
Avg cluster size: 20080.00


/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [43]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.5607965713297417 ms

Accuracy: 46.0
Positives Recall: 100.0
Positives Precision: 46.0
Positives F1: 63.0
Distance:  0.38
Max cluster size:  19096
Median cluster size:  19096
Avg cluster size: 19096.00


/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Any application of the complex loss doesn't give an accaptable result.

###Single loss Distilation

Further experiments are based on the single loss function approach. For this functions were chosen MSE and Cosine similarity evaluations.

####Modeling and Preprocessing

In [4]:
%cd /content/drive/MyDrive/NewsBert
from initial_finetuned_model import ClusteringTripletModel
from loading_and_evaluation import gen_batch, records_to_embeds, get_quality, NewsDataset, get_loaders

with open('single_full_train_embeddings_bert', 'rb') as pickle_file:
    single_full_train_embeddings_bert = pickle.load(pickle_file)

with open('single_full_val_embeddings_bert', 'rb') as pickle_file:
    single_full_val_embeddings_bert = pickle.load(pickle_file)


with open('full_train_records', 'rb') as pickle_file:
    full_train_records = pickle.load(pickle_file)

with open('full_val_records', 'rb') as pickle_file:
    full_val_records = pickle.load(pickle_file)


with open('public_set', 'rb') as pickle_file:
    public_set = pickle.load(pickle_file)

with open('private_set', 'rb') as pickle_file:
    private_set = pickle.load(pickle_file)


initial_model = ClusteringTripletModel.load_from_checkpoint(
    model_path = INITIAL_MODEL,
    checkpoint_path = '/content/drive/MyDrive/NewsBert/best_clustering_news_bert-val_loss=0.0008.ckpt',
    num_training_steps = None
    )

embedder = initial_model.embedder.cuda()

VOCAB_SIZE = embedder.model.embeddings.word_embeddings.num_embeddings
BATCH_SIZE = 128


public_markup = read_markup_tsv("ru_clustering_0527_urls_final.tsv")
private_markup = read_markup_tsv("ru_clustering_0529_urls_final_v2.tsv")

/content/drive/MyDrive/NewsBert


Downloading:   0%|          | 0.00/831 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/679M [00:00<?, ?B/s]

Some weights of the model checkpoint at IlyaGusev/news_tg_rubert were not used when initializing BertModel: ['cls.predictions.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertModel were not initialized from the model checkpoint at IlyaGusev/news_tg_rubert and are newly initialized: ['bert.pooler.dense.weight', 'bert.pooler.dense.

In [5]:
class SingleClusteringDistillModel(nn.Module):
    def __init__(self, vocab_size, target_size=TARGET_SIZE, 
                 bidirectional=False, pretrained=False, 
                 word_emb_dim=128, pretrained_embs=None, 
                 freeze_pretrained=False, evaluate_similarity=False,
                 rnn_hidden_dim=128, rnn_layers_count=1, 
                 dropout=0.3, lr=1e-3, add_relu=False,
                 del_linear=False, to_rnn=False, 
                 to_gru=False, del_2_linear=False, 
                 attentive_aggregation=False,
                 ):
      
        super().__init__()

        self.embedder = LSTM_Embedder(vocab_size=vocab_size, 
                                      target_size=target_size, 
                                      bidirectional=bidirectional, 
                                      word_emb_dim=word_emb_dim, 
                                      rnn_hidden_dim=rnn_hidden_dim, 
                                      rnn_layers_count=rnn_layers_count,
                                      pretrained=pretrained, 
                                      pretrained_embs=pretrained_embs, 
                                      freeze_pretrained=freeze_pretrained,
                                      dropout=dropout, add_relu=add_relu, 
                                      del_linear=del_linear, to_rnn=to_rnn,
                                      to_gru=to_gru,
                                      del_2_linear=del_2_linear,
                                      attentive_aggregation=attentive_aggregation,
                                      )

        self.evaluate_similarity = evaluate_similarity
        if not evaluate_similarity:
          self.mse = torch.nn.MSELoss()
        else:
          self.cosine_similarity = torch.nn.functional.cosine_similarity
        
        self.lr = lr

    def forward(self, news):
        embeddings = self.embedder(news["input_ids"].cuda(), news["attention_mask"])
        return embeddings

    def loss(self, embeds, bert_embeds):
        if self.evaluate_similarity is True:
          similarity = self.cosine_similarity(embeds, bert_embeds)
          loss = torch.mean(torch.ones(len(similarity)).cuda() - similarity)
        else:
          loss = self.mse(embeds.float(), bert_embeds.float())
        return loss

In [6]:
train_loader, val_loader, tokenizer = get_loaders(full_train_records,
                                                  full_val_records, 
                                                  INITIAL_MODEL, MAX_TOKENS, 
                                                  BATCH_SIZE, 
                                                  single_full_train_embeddings_bert,
                                                  single_full_val_embeddings_bert,
                                                  )                                       

Downloading:   0%|          | 0.00/1.57M [00:00<?, ?B/s]

####Experiments: Simple LSTM - MSE/Cosine similarity loss


In [ ]:
single_lstm_distill = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE)
train(single_lstm_distill, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_MSE/LSTM',
      )

Train: 100%|██████████| 4037/4037 [06:21<00:00, 10.59it/s]


Train_loss:  0.0030305164414906683


Val: 100%|██████████| 1010/1010 [01:32<00:00, 10.93it/s]


Val_loss:  0.0025779105065906844


Train: 100%|██████████| 4037/4037 [06:25<00:00, 10.46it/s]


...

Val_loss:  0.001578715230144634


Train: 100%|██████████| 4037/4037 [06:22<00:00, 10.56it/s]


Train_loss:  0.0017747614231765278


Val: 100%|██████████| 1010/1010 [01:23<00:00, 12.07it/s]


Val_loss:  0.001575955296151967


In [ ]:
single_lstm_distill = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE)
single_lstm_distill.load_state_dict(torch.load('/content/drive/MyDrive/NewsBert/Distillation_MSE/LSTM/best-distill-bert.pt'))

distill_embedder = single_lstm_distill.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.6796909511326794 ms

Accuracy: 91.9
Positives Recall: 92.8
Positives Precision: 90.0
Positives F1: 91.4
Distance:  0.38
Max cluster size:  304
Median cluster size:  2.0
Avg cluster size: 5.75


In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.6796732293320941 ms

Accuracy: 92.2
Positives Recall: 94.1
Positives Precision: 89.5
Positives F1: 91.8
Distance:  0.38
Max cluster size:  172
Median cluster size:  2
Avg cluster size: 5.52


In [ ]:
single_lstm_distill_cos_similarity = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE, 
                                                                  evaluate_similarity=True)
train(single_lstm_distill_cos_similarity, train_loader, val_loader,
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/LSTM',
      )

Train: 100%|██████████| 4037/4037 [06:19<00:00, 10.63it/s]


Train_loss:  0.4933299220963145


Val: 100%|██████████| 1010/1010 [01:24<00:00, 12.02it/s]


Val_loss:  0.35678940173006213


Train: 100%|██████████| 4037/4037 [06:14<00:00, 10.77it/s]


...

Val_loss:  0.17594625835229558


Train: 100%|██████████| 4037/4037 [06:15<00:00, 10.76it/s]


Train_loss:  0.21959078252665573


Val: 100%|██████████| 1010/1010 [01:23<00:00, 12.14it/s]


Val_loss:  0.17483822996592882


In [ ]:
single_lstm_distill_cos_similarity = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE, 
                                                                   evaluate_similarity=True)

single_lstm_distill_cos_similarity.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/LSTM/best-distill-bert.pt'))


distill_embedder = single_lstm_distill_cos_similarity.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.6773523045726031 ms

Accuracy: 92.9
Positives Recall: 93.6
Positives Precision: 91.3
Positives F1: 92.4
Distance:  0.38
Max cluster size:  303
Median cluster size:  2
Avg cluster size: 5.07


In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.6771633880978406 ms

Accuracy: 93.0
Positives Recall: 94.3
Positives Precision: 90.9
Positives F1: 92.6
Distance:  0.38
Max cluster size:  172
Median cluster size:  2.0
Avg cluster size: 4.84


####Experiments: Bidirectional LSTM - MSE/Cosine similarity loss

In [ ]:
lstm_bidir_distill = SingleClusteringDistillModel(VOCAB_SIZE, bidirectional=True)

train(lstm_bidir_distill, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_MSE/LSTM_Bidir',
      )

Train: 100%|██████████| 4037/4037 [08:01<00:00,  8.38it/s]


Train_loss:  0.0029044680659914587


Val: 100%|██████████| 1010/1010 [02:31<00:00,  6.69it/s]


Val_loss:  0.0024208000199500436


Train: 100%|██████████| 4037/4037 [10:47<00:00,  6.23it/s]


...

Val_loss:  0.001363272115814103


Train: 100%|██████████| 4037/4037 [08:29<00:00,  7.93it/s]


Train_loss:  0.0015060103383396954


Val: 100%|██████████| 1010/1010 [02:56<00:00,  5.72it/s]


Val_loss:  0.0013541400570901904


In [ ]:
lstm_bidir_distill = SingleClusteringDistillModel(VOCAB_SIZE, bidirectional=True)

lstm_bidir_distill.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_MSE/LSTM_Bidir/best-distill-bert.pt'))

distill_embedder = lstm_bidir_distill.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.817096007012751 ms

Accuracy: 92.8
Positives Recall: 93.8
Positives Precision: 90.9
Positives F1: 92.3
Distance:  0.38
Max cluster size:  290
Median cluster size:  2
Avg cluster size: 4.82


In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.8396399011659882 ms

Accuracy: 92.8
Positives Recall: 94.5
Positives Precision: 90.3
Positives F1: 92.3
Distance:  0.38
Max cluster size:  152
Median cluster size:  2
Avg cluster size: 4.65


In [ ]:
bidir_lstm_distill_cos_similarity = SingleClusteringDistillModel(VOCAB_SIZE, 
                                                                bidirectional=True,
                                                                evaluate_similarity=True)
train(bidir_lstm_distill_cos_similarity, train_loader, val_loader,
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM',
      )

Train: 100%|██████████| 4037/4037 [07:45<00:00,  8.68it/s]


Train_loss:  0.4637804734371837


Val: 100%|██████████| 1010/1010 [01:45<00:00,  9.57it/s]


Val_loss:  0.33067102834380235


Train: 100%|██████████| 4037/4037 [07:42<00:00,  8.73it/s]


...

Val_loss:  0.15720947974293886


Train: 100%|██████████| 4037/4037 [07:27<00:00,  9.02it/s]


Train_loss:  0.17848591986685122


Val: 100%|██████████| 1010/1010 [01:44<00:00,  9.69it/s]


Val_loss:  0.15634259718434693


In [ ]:
bidir_lstm_distill_cos_similarity = SingleClusteringDistillModel(VOCAB_SIZE, 
                                                                bidirectional=True,
                                                                evaluate_similarity=True)

bidir_lstm_distill_cos_similarity.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM/best-distill-bert.pt'))


distill_embedder = bidir_lstm_distill_cos_similarity.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.8570194378079646 ms

Accuracy: 93.5
Positives Recall: 94.6
Positives Precision: 91.6
Positives F1: 93.0
Distance:  0.38
Max cluster size:  294
Median cluster size:  2
Avg cluster size: 4.58


In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.8509773509393539 ms

Accuracy: 93.1
Positives Recall: 94.7
Positives Precision: 90.7
Positives F1: 92.6
Distance:  0.38
Max cluster size:  158
Median cluster size:  2.0
Avg cluster size: 4.40


####Experiments: Bidirectional LSTM - MSE/Cosine similarity loss - pretrained



In [ ]:
pretrained_embs = initial_model.embedder.model.embeddings.word_embeddings.weight.cuda()

lstm_bidir_distill_from_pretrained = SingleClusteringDistillModel(VOCAB_SIZE, bidirectional=True,
                                                                   pretrained=True, 
                                                                   pretrained_embs=pretrained_embs)

train(lstm_bidir_distill_from_pretrained, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_MSE/LSTM_Bidir_from_pretrained',
      )

Train: 100%|██████████| 4037/4037 [10:56<00:00,  6.15it/s]


Train_loss:  0.001778852204352263


Val: 100%|██████████| 1010/1010 [01:53<00:00,  8.89it/s]


Val_loss:  0.0011222380471627902


Train: 100%|██████████| 4037/4037 [10:54<00:00,  6.17it/s]


...

Val_loss:  0.0008293005286849629


Train: 100%|██████████| 4037/4037 [09:45<00:00,  6.90it/s]


Train_loss:  0.0009438869977833143


Val: 100%|██████████| 1010/1010 [01:49<00:00,  9.24it/s]


Val_loss:  0.0008236844883309586


In [ ]:
pretrained_embs = initial_model.embedder.model.embeddings.word_embeddings.weight.cuda()

lstm_bidir_distill_from_pretrained = SingleClusteringDistillModel(VOCAB_SIZE, bidirectional=True,
                                                                   pretrained=True, 
                                                                   pretrained_embs=pretrained_embs)

lstm_bidir_distill_from_pretrained.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_MSE/LSTM_Bidir_from_pretrained/best-distill-bert.pt'))

distill_embedder = lstm_bidir_distill_from_pretrained.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.9751229351497741 ms

Accuracy: 94.4
Positives Recall: 95.7
Positives Precision: 92.4
Positives F1: 94.0
Distance:  0.38
Max cluster size:  273
Median cluster size:  2.0
Avg cluster size: 4.06


In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.9897823068053841 ms

Accuracy: 93.9
Positives Recall: 96.0
Positives Precision: 91.2
Positives F1: 93.5
Distance:  0.38
Max cluster size:  172
Median cluster size:  2.0
Avg cluster size: 3.89


In [ ]:
pretrained_embs = initial_model.embedder.model.embeddings.word_embeddings.weight.cuda()

bidir_lstm_distill_cos_similarity_from_pretrained = SingleClusteringDistillModel(VOCAB_SIZE, 
                                                                bidirectional=True,
                                                                evaluate_similarity=True,
                                                                pretrained=True, 
                                                                pretrained_embs=pretrained_embs)
train(bidir_lstm_distill_cos_similarity_from_pretrained, train_loader, val_loader,
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_from_pretrained',
      )

Train: 100%|██████████| 4037/4037 [10:12<00:00,  6.59it/s]


Train_loss:  0.1826794395580551


Val: 100%|██████████| 1010/1010 [01:45<00:00,  9.56it/s]


Val_loss:  0.11902867370785407


Train: 100%|██████████| 4037/4037 [10:02<00:00,  6.70it/s]


...

Val_loss:  0.10341306113041898


Train: 100%|██████████| 4037/4037 [09:49<00:00,  6.85it/s]


Train_loss:  0.11701886377541372


Val: 100%|██████████| 1010/1010 [01:44<00:00,  9.66it/s]


Val_loss:  0.10356812516954504


In [ ]:
bidir_lstm_distill_cos_similarity_from_pretrained = SingleClusteringDistillModel(VOCAB_SIZE, 
                                                                bidirectional=True,
                                                                evaluate_similarity=True,
                                                                pretrained=True, 
                                                                pretrained_embs=pretrained_embs)

bidir_lstm_distill_cos_similarity_from_pretrained.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_from_pretrained/best-distill-bert.pt'))

distill_embedder = bidir_lstm_distill_cos_similarity_from_pretrained.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.8325269604821605 ms

Accuracy: 94.4
Positives Recall: 95.6
Positives Precision: 92.5
Positives F1: 94.0
Distance:  0.38
Max cluster size:  270
Median cluster size:  2.0
Avg cluster size: 4.00


In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.8566778560637629 ms

Accuracy: 93.4
Positives Recall: 95.2
Positives Precision: 90.9
Positives F1: 93.0
Distance:  0.38
Max cluster size:  184
Median cluster size:  2.0
Avg cluster size: 3.88


####Experiments: Bidirectional LSTM - Cosine similarity loss - pretrained alike



It's reasonable to check if pretrained embeds are really impacting the score or the key for a better result is the size of initial word embeddings.

In [ ]:
#Checking random initialization similar to pretrained 

pretrained_embs = initial_model.embedder.model.embeddings.word_embeddings.weight.cuda()
word_embs_dim = pretrained_embs.shape[1] 

bidir_lstm_distill_from_pretrained_alike = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, word_emb_dim=word_embs_dim,
                              evaluate_similarity=True)


train(bidir_lstm_distill_from_pretrained_alike, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_from_pretrained_alike',
      )

Train: 100%|██████████| 4037/4037 [07:43<00:00,  8.70it/s]


Train_loss:  0.3719831273995782


Val: 100%|██████████| 1010/1010 [01:39<00:00, 10.18it/s]


Val_loss:  0.24544119784002452


Train: 100%|██████████| 4037/4037 [07:40<00:00,  8.76it/s]


...

Val_loss:  0.14750357786226623


Train: 100%|██████████| 4037/4037 [07:45<00:00,  8.68it/s]


Train_loss:  0.16164504280356584


Val: 100%|██████████| 1010/1010 [01:41<00:00,  9.98it/s]


Val_loss:  0.14721872530049043


In [ ]:
word_embs_dim = pretrained_embs.shape[1] 

bidir_lstm_distill_from_pretrained_alike = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, word_emb_dim=word_embs_dim,
                              evaluate_similarity=True)

bidir_lstm_distill_from_pretrained_alike.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_from_pretrained_alike/best-distill-bert.pt'))

distill_embedder = bidir_lstm_distill_from_pretrained_alike.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.9082841508179547 ms

Accuracy: 93.2
Positives Recall: 94.2
Positives Precision: 91.4
Positives F1: 92.8
Distance:  0.38
Max cluster size:  310
Median cluster size:  2.0
Avg cluster size: 4.30


In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.8422611976548824 ms

Accuracy: 93.0
Positives Recall: 94.6
Positives Precision: 90.6
Positives F1: 92.6
Distance:  0.38
Max cluster size:  200
Median cluster size:  2
Avg cluster size: 4.17


So, it turns out that pretrained embeddings really improve performance, but models based on pretrained embeds are much heavier. 

In general BiLSTM with Cosine embedding loss work mostly better.

####Experiments: Bidirectional LSTM - Cosine similarity loss - variations

Some more architecture and parameters experiments with a bidirectional LSTM.

#####Adding ReLU between linear layers

In [ ]:
bidir_lstm_cosine_similarity_distill_relu = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, add_relu=True, evaluate_similarity=True)


train(bidir_lstm_cosine_similarity_distill_relu, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_relu',
      )

Train: 100%|██████████| 4037/4037 [08:43<00:00,  7.71it/s]


Train_loss:  0.4517234906723245


Val: 100%|██████████| 1010/1010 [01:47<00:00,  9.36it/s]


Val_loss:  0.3223376839308669


Train: 100%|██████████| 4037/4037 [08:17<00:00,  8.12it/s]


...

Val_loss:  0.15698775316053482


Train: 100%|██████████| 4037/4037 [07:43<00:00,  8.70it/s]


Train_loss:  0.16261611715219093


Val: 100%|██████████| 1010/1010 [01:43<00:00,  9.79it/s]


Val_loss:  0.15645668499204396


In [ ]:
bidir_lstm_cosine_similarity_distill_relu = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, add_relu=True, evaluate_similarity=True)

bidir_lstm_cosine_similarity_distill_relu.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_relu/best-distill-bert.pt'))

distill_embedder = bidir_lstm_cosine_similarity_distill_relu.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, 
                                              tokenizer, batch_size=8, max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.9087116057416832 ms

Accuracy: 92.3
Positives Recall: 93.2
Positives Precision: 90.3
Positives F1: 91.7
Distance:  0.38
Max cluster size:  318
Median cluster size:  2
Avg cluster size: 5.31


In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.9416431484234398 ms

Accuracy: 91.6
Positives Recall: 92.9
Positives Precision: 89.2
Positives F1: 91.0
Distance:  0.38
Max cluster size:  159
Median cluster size:  2
Avg cluster size: 5.16


#####Zero dropout

In [ ]:
bidir_lstm_distill_dropout0 = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                               bidirectional=True, dropout=0, evaluate_similarity=True,)


train(bidir_lstm_distill_dropout0, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_dropout0',
      )

Train: 100%|██████████| 4037/4037 [06:32<00:00, 10.27it/s]


Train_loss:  0.4113105625619639


Val: 100%|██████████| 1010/1010 [01:28<00:00, 11.41it/s]


Val_loss:  0.2967117350732604


Train: 100%|██████████| 4037/4037 [06:34<00:00, 10.23it/s]


...

Val_loss:  0.13266496468600236


Train: 100%|██████████| 4037/4037 [06:29<00:00, 10.36it/s]


Train_loss:  0.10601139769321848


Val: 100%|██████████| 1010/1010 [01:26<00:00, 11.62it/s]


Val_loss:  0.13188875619896936


In [ ]:
bidir_lstm_distill_dropout0 = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                               bidirectional=True, dropout=0, evaluate_similarity=True,)

bidir_lstm_distill_dropout0.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_dropout0/best-distill-bert.pt'))

distill_embedder = bidir_lstm_distill_dropout0.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, 
                                              tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.7914375324648215 ms

Accuracy: 93.8
Positives Recall: 95.0
Positives Precision: 91.9
Positives F1: 93.4
Distance:  0.38
Max cluster size:  297
Median cluster size:  2.0
Avg cluster size: 3.80


In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.8030722337534201 ms

Accuracy: 93.5
Positives Recall: 95.6
Positives Precision: 90.7
Positives F1: 93.1
Distance:  0.38
Max cluster size:  170
Median cluster size:  2.0
Avg cluster size: 3.69


#####Zero dropout + deleted linear

In [ ]:
bidir_lstm_distill_dropout0_del_linear = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              dropout=0, evaluate_similarity=True,
                              del_linear=True, bidirectional=True)


train(bidir_lstm_distill_dropout0_del_linear, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_dropout0_del_linear',
      )

In [ ]:
bidir_lstm_distill_dropout0_del_linear = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              dropout=0, evaluate_similarity=True,
                              del_linear=True, bidirectional=True)

bidir_lstm_distill_dropout0_del_linear.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_dropout0_del_linear/best-distill-bert.pt'))

distill_embedder = bidir_lstm_distill_dropout0_del_linear.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.7941229934948849 ms

Accuracy: 93.8
Positives Recall: 94.5
Positives Precision: 92.3
Positives F1: 93.4
Distance:  0.38
Max cluster size:  332
Median cluster size:  2.0
Avg cluster size: 3.73


In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.7835019862846595 ms

Accuracy: 93.1
Positives Recall: 94.2
Positives Precision: 91.0
Positives F1: 92.6
Distance:  0.38
Max cluster size:  164
Median cluster size:  2
Avg cluster size: 3.62


#####Zero dropout + deleted linear + *attentive aggregation*

In [ ]:
bidir_lstm_distill_dropout0_del_linear_attn = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              dropout=0, evaluate_similarity=True,
                              del_linear=True, bidirectional=True, 
                              attentive_aggregation=True)


train(bidir_lstm_distill_dropout0_del_linear_attn, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_dropout0_del_linear_attn',
      )

In [20]:
bidir_lstm_distill_dropout0_del_linear_attn = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              dropout=0, evaluate_similarity=True,
                              del_linear=True, bidirectional=True,
                              attentive_aggregation=True)

bidir_lstm_distill_dropout0_del_linear_attn.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_dropout0_del_linear_attn/best-distill-bert.pt'))

distill_embedder = bidir_lstm_distill_dropout0_del_linear_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.6317020336470281 ms

Accuracy: 94.2
Positives Recall: 95.2
Positives Precision: 92.5
Positives F1: 93.8
Distance:  0.38
Max cluster size:  262
Median cluster size:  2.0
Avg cluster size: 3.86


In [22]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.7009760991369375 ms

Accuracy: 93.7
Positives Recall: 95.2
Positives Precision: 91.6
Positives F1: 93.3
Distance:  0.38
Max cluster size:  171
Median cluster size:  2
Avg cluster size: 3.73


#####Zero dropout / LSTM with no linear layers

In [ ]:
bidir_lstm_distill_dropout0_del_2_linear = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, lstm_hidden_dim=(TARGET_SIZE//2),
                              del_2_linear=True, evaluate_similarity=True,
                              )

train(bidir_lstm_distill_dropout0_del_2_linear, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_no_linear_0_dropout',
      )

Train: 100%|██████████| 4037/4037 [06:00<00:00, 11.20it/s]


Train_loss:  0.45590375669868366


Val: 100%|██████████| 1010/1010 [01:21<00:00, 12.38it/s]


Val_loss:  0.33710911709989144


Train: 100%|██████████| 4037/4037 [06:09<00:00, 10.94it/s]


...

Val_loss:  0.1415595237204064


Train: 100%|██████████| 4037/4037 [06:02<00:00, 11.13it/s]


Train_loss:  0.11628820423808249


Val: 100%|██████████| 1010/1010 [01:22<00:00, 12.22it/s]


Val_loss:  0.14016308501422575


In [ ]:
bidir_lstm_distill_dropout0_del_2_linear = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, lstm_hidden_dim=(TARGET_SIZE//2),
                              del_2_linear=True, evaluate_similarity=True,
                              )

bidir_lstm_distill_dropout0_del_2_linear.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_no_linear_0_dropout/best-distill-bert.pt'))

distill_embedder = bidir_lstm_distill_dropout0_del_2_linear.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.7147467624143775 ms


0.9301095579901776

In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

#####Zero dropout / LSTM with no linear layers + *attentive aggregation*

In [ ]:
bidir_lstm_distill_dropout0_del_2_linear_attn = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, lstm_hidden_dim=(TARGET_SIZE//2),
                              del_2_linear=True, evaluate_similarity=True,
                              attentive_aggregation=True,
                              )

train(bidir_lstm_distill_dropout0_del_2_linear_attn, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_no_linear_0_dropout_attn',
      )

In [11]:
bidir_lstm_distill_dropout0_del_2_linear_attn = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, lstm_hidden_dim=(TARGET_SIZE//2),
                              del_2_linear=True, evaluate_similarity=True,
                              attentive_aggregation=True,
                              )

bidir_lstm_distill_dropout0_del_2_linear_attn.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_no_linear_0_dropout_attn/best-distill-bert.pt'))

distill_embedder = bidir_lstm_distill_dropout0_del_2_linear_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.6654116432980237 ms

Accuracy: 93.7
Positives Recall: 94.3
Positives Precision: 92.3
Positives F1: 93.3
Distance:  0.38
Max cluster size:  256
Median cluster size:  2
Avg cluster size: 3.84


In [12]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.6268822015030993 ms

Accuracy: 93.3
Positives Recall: 94.6
Positives Precision: 91.2
Positives F1: 92.9
Distance:  0.38
Max cluster size:  167
Median cluster size:  2
Avg cluster size: 3.70


#####Zero dropout + deleted linear + 2 LSTM layers

In [ ]:
bidir_lstm_distill_dropout0_del_2lstm_layers = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, 
                              del_linear=True, evaluate_similarity=True,
                              lstm_layers_count=2,
                              )


train(bidir_lstm_distill_dropout0_del_2lstm_layers, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_2layers',
      )

Train: 100%|██████████| 4037/4037 [07:46<00:00,  8.65it/s]


Train_loss:  0.38224130868686124


Val: 100%|██████████| 1010/1010 [01:28<00:00, 11.37it/s]


Val_loss:  0.25747238826928553


Train: 100%|██████████| 4037/4037 [07:48<00:00,  8.62it/s]


...

Val_loss:  0.1147477903493117


Train: 100%|██████████| 4037/4037 [07:50<00:00,  8.58it/s]


Train_loss:  0.08808871829908632


Val: 100%|██████████| 1010/1010 [01:27<00:00, 11.55it/s]


Val_loss:  0.11444825672888713


In [ ]:
bidir_lstm_distill_dropout0_del_2lstm_layers = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, 
                              del_linear=True, evaluate_similarity=True,
                              lstm_layers_count=2)

bidir_lstm_distill_dropout0_del_2lstm_layers.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_2layers/best-distill-bert.pt'))

distill_embedder = bidir_lstm_distill_dropout0_del_2lstm_layers.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.3904166992442066 ms

Accuracy: 94.2
Positives Recall: 95.5
Positives Precision: 92.3
Positives F1: 93.9
Distance:  0.38
Max cluster size:  293
Median cluster size:  2
Avg cluster size: 4.08


In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.4165139411801217 ms

Accuracy: 93.5
Positives Recall: 95.7
Positives Precision: 90.7
Positives F1: 93.1
Distance:  0.38
Max cluster size:  176
Median cluster size:  2.0
Avg cluster size: 3.94


#####Zero dropout + deleted linear + 2 LSTM layers + *attentive aggregation*

In [ ]:
bidir_lstm_distill_dropout0_del_2lstm_layers_attn = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, 
                              del_linear=True, evaluate_similarity=True,
                              lstm_layers_count=2,
                              attentive_aggregation=True,
                              )


train(bidir_lstm_distill_dropout0_del_2lstm_layers_attn, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_2layers_attn',
      )

In [13]:
bidir_lstm_distill_dropout0_del_2lstm_layers_attn = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, 
                              del_linear=True, evaluate_similarity=True,
                              lstm_layers_count=2,
                              attentive_aggregation=True,)

bidir_lstm_distill_dropout0_del_2lstm_layers_attn.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_LSTM_2layers_attn/best-distill-bert.pt'))

distill_embedder = bidir_lstm_distill_dropout0_del_2lstm_layers_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.1977450613006653 ms

Accuracy: 94.3
Positives Recall: 95.3
Positives Precision: 92.5
Positives F1: 93.9
Distance:  0.38
Max cluster size:  283
Median cluster size:  2
Avg cluster size: 4.07


In [14]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.1479616358183296 ms

Accuracy: 93.8
Positives Recall: 95.7
Positives Precision: 91.3
Positives F1: 93.4
Distance:  0.38
Max cluster size:  176
Median cluster size:  2
Avg cluster size: 3.92


##--Comparisons--

###Single loss on the original data

In [58]:
labeled_train_recs_single = dict()

for i in train_records:
  for j in i:
    labeled_train_recs_single[j['url']] = j

labeled_train_recs_single = list(labeled_train_recs_single.values())

In [59]:
labeled_val_recs_single = dict()

for i in val_records:
  for j in i:
    labeled_val_recs_single[j['url']] = j

labeled_val_recs_single = list(labeled_val_recs_single.values())

In [62]:
labeled_val_embeddings_bert = records_to_embeds(labeled_val_recs_single, embedder, 
                                          initial_tokenizer, batch_size=8, 
                                          max_tokens_count=MAX_TOKENS)
labeled_train_embeddings_bert = records_to_embeds(labeled_train_recs_single, embedder, 
                                            initial_tokenizer, batch_size=8, 
                                            max_tokens_count=MAX_TOKENS)

In [63]:
BATCH_SIZE = 32

train_loader_labeled, val_loader_labeled, tokenizer_triplets = get_loaders(
                                       labeled_train_recs_single, 
                                       labeled_val_recs_single, 
                                       INITIAL_MODEL, MAX_TOKENS, 
                                       BATCH_SIZE, labeled_train_embeddings_bert,
                                       labeled_val_embeddings_bert,
                                       )

In [44]:
single_labeled_data_lstm = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE)


train(single_labeled_data_lstm, train_loader_labeled, val_loader_labeled, 
      100, '/content/drive/MyDrive/NewsBert/Comparisons/single_labeled_data_lstm',
      True)

Train: 100%|██████████| 362/362 [00:11<00:00, 31.73it/s]


Train_loss:  0.003719133842036704


Val: 100%|██████████| 185/185 [00:05<00:00, 36.98it/s]


Val_loss:  0.003459727404186049


Train: 100%|██████████| 362/362 [00:11<00:00, 31.26it/s]


...

Val_loss:  0.0008903047733789159


Train: 100%|██████████| 362/362 [00:11<00:00, 31.68it/s]


Train_loss:  0.0012224457636398382


Val: 100%|██████████| 185/185 [00:04<00:00, 37.41it/s]


Val_loss:  0.0008917170532702192


In [45]:
single_labeled_data_lstm.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Comparisons/single_labeled_data_lstm/best-distill-bert.pt'))

distill_embedder = single_labeled_data_lstm.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer_triplets, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.5495348462426805 ms

Accuracy: 72.2
Positives Recall: 41.2
Positives Precision: 96.5
Positives F1: 57.7
Distance:  0.38
Max cluster size:  109
Median cluster size:  1.0
Avg cluster size: 1.85


In [46]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer_triplets, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.5597209411157841 ms

Accuracy: 71.5
Positives Recall: 39.6
Positives Precision: 96.1
Positives F1: 56.1
Distance:  0.38
Max cluster size:  79
Median cluster size:  1
Avg cluster size: 1.82


###Comparisons for the final estimation

In [46]:
class ClusteringTripletModelForLSTM(nn.Module):
    def __init__(self, vocab_size=119547,  
                 word_emb_dim=128, 
                 rnn_hidden_dim=128,
                 rnn_layers_count=2,
                 target_size=TARGET_SIZE, 
                 lr=1e-3, 
                 margin=0.5,
                 to_gru=False,
                 attentive_aggregation=False,
                 ):
        super().__init__()

        self.embedder = DistillEmbedder(vocab_size=vocab_size, 
                                        word_emb_dim=word_emb_dim, 
                                        rnn_hidden_dim=rnn_hidden_dim, 
                                        rnn_layers_count=rnn_layers_count,
                                        target_size=target_size,
                                        to_gru=to_gru,
                                        attentive_aggregation=attentive_aggregation,
                                        )


        self.triplet_loss = nn.TripletMarginWithDistanceLoss(
            margin=margin,
            distance_function=nn.PairwiseDistance(p=2)
        )

        self.lr = lr

    def forward(self, pivots, positives, negatives):
        pivot_embeddings = self.embedder(pivots["input_ids"].cuda(), pivots["attention_mask"])
        positive_embeddings = self.embedder(positives["input_ids"].cuda(), positives["attention_mask"])
        negative_embeddings = self.embedder(negatives["input_ids"].cuda(), negatives["attention_mask"])
        return pivot_embeddings, positive_embeddings, negative_embeddings

    def loss(self, embeds, bert_embeds):
        anchor, positive, negative = embeds
        triplet_loss = self.triplet_loss(anchor, positive, negative) 
        return triplet_loss


def epoch_train(model, data_loader, optimizer, scheduler):
    train_loss = 0
    model.cuda().train()
    for i, samples in enumerate(tqdm(data_loader, desc='Train')):
       model.zero_grad()
       
       bert_embeds = [samples[3].cuda(), samples[4].cuda(), samples[5].cuda()]
       embeds = model(samples[0], samples[1], samples[2])


       loss = model.loss(embeds, bert_embeds)
       loss.backward()
       optimizer.step()
       train_loss += float(loss)
    loss = train_loss / len(data_loader)
    scheduler.step(loss)
    print('Train_loss: ', loss)
    return loss

def train(model, train_data_loader,
          val_data_loader, num_train_epochs, 
          output_dir, optimizer=torch.optim.Adam, 
          patience=3, scheduler_patience=2, 
          ):
      optimizer = optimizer(model.parameters(), lr=model.lr)
      scheduler = ReduceLROnPlateau(optimizer, patience=scheduler_patience)
      writer = SummaryWriter(output_dir)
      best_val_loss = 100000
      best_count = 0
      for epoch in range(num_train_epochs):
          train_loss = epoch_train(model, train_data_loader, optimizer, scheduler)
          val_loss = epoch_val(model, val_data_loader)
          writer.add_scalar('Loss/train', train_loss, epoch)
          writer.add_scalar('Loss/val', val_loss, epoch)
          writer.add_scalar('Learning rate', scheduler._last_lr[0], epoch)
          best_count += 1
         
          if val_loss < best_val_loss:
              best_val_loss = val_loss
              best_count = 0
              torch.save(model.state_dict(), os.path.join(output_dir, f'best-distill-bert.pt'))
          
          if best_count == patience:
              torch.save(model.state_dict(), os.path.join(output_dir, 'last_epoch.pt'))
              writer.close()
              break

      writer.close()
      torch.save(model.state_dict(), os.path.join(output_dir, 'last_epoch.pt'))

In [54]:
BATCH_SIZE = 32

bidir_gru_not_distilled = ClusteringTripletModelForLSTM(attentive_aggregation=True, to_gru=True)


train(bidir_gru_not_distilled, train_loader_triplets, val_loader_triplets,  
      60, '/content/drive/MyDrive/NewsBert/Comparisons/bidir_gru_not_distilled_attn',
      )

Train: 100%|██████████| 471/471 [01:16<00:00,  6.15it/s]


Train_loss:  0.09177566635285973


Val: 100%|██████████| 118/118 [00:11<00:00, 10.44it/s]


Val_loss:  0.04990701967755617


Train: 100%|██████████| 471/471 [01:16<00:00,  6.16it/s]


...

Val_loss:  0.03871551689581346


Train: 100%|██████████| 471/471 [01:16<00:00,  6.13it/s]


Train_loss:  0.004518746428049294


Val: 100%|██████████| 118/118 [00:11<00:00, 10.32it/s]


Val_loss:  0.04083520155084335


In [33]:
bidir_gru_not_distilled.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Comparisons/bidir_gru_not_distilled_attn/best-distill-bert.pt'))

distill_embedder = bidir_gru_not_distilled.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer_triplets, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.5357810535278928 ms

Accuracy: 46.2
Positives Recall: 100.0
Positives Precision: 46.2
Positives F1: 63.2
Distance:  0.38
Max cluster size:  20059
Median cluster size:  3
Avg cluster size: 2868.57


In [34]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer_triplets, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.5504345593714144 ms

Accuracy: 45.9
Positives Recall: 99.7
Positives Precision: 45.9
Positives F1: 62.9
Distance:  0.38
Max cluster size:  19068
Median cluster size:  9
Avg cluster size: 3819.20


In [21]:
BATCH_SIZE = 32

bidir_gru_not_distilled_64 = ClusteringTripletModelForLSTM(attentive_aggregation=True, to_gru=True,
                                                           word_emb_dim=64)


train(bidir_gru_not_distilled_64, train_loader_triplets, val_loader_triplets,  
      60, '/content/drive/MyDrive/NewsBert/Comparisons/bidir_gru_not_distilled_attn/64',
      )

Train: 100%|██████████| 471/471 [01:17<00:00,  6.11it/s]


Train_loss:  0.10535618780683054


Val: 100%|██████████| 118/118 [00:11<00:00, 10.13it/s]


Val_loss:  0.06566119653377998


Train: 100%|██████████| 471/471 [01:16<00:00,  6.12it/s]


...

Val_loss:  0.04008224215042793


Train: 100%|██████████| 471/471 [01:17<00:00,  6.10it/s]


Train_loss:  0.004059622020731559


Val: 100%|██████████| 118/118 [00:11<00:00, 10.28it/s]


Val_loss:  0.044734745081198415


In [47]:
bidir_gru_not_distilled_64.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Comparisons/bidir_gru_not_distilled_attn/64/best-distill-bert.pt'))

distill_embedder = bidir_gru_not_distilled_64.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer_triplets, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.5908298339026858 ms

Accuracy: 54.2
Positives Recall: 62.4
Positives Precision: 50.3
Positives F1: 55.7
Distance:  0.38
Max cluster size:  13618
Median cluster size:  14
Avg cluster size: 542.70


In [48]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer_triplets, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.536950621936528 ms

Accuracy: 57.7
Positives Recall: 71.9
Positives Precision: 53.0
Positives F1: 61.0
Distance:  0.38
Max cluster size:  14934
Median cluster size:  19
Avg cluster size: 578.67


In [ ]:
EPOCHS = 60
ACCUMULATE_GRAD_BATCHES = 8
LOG_EVERY_N_STEPS = 10

In [ ]:
BATCH_SIZE = 12

tiny_train_loader, tiny_val_loader, tiny_tokenizer = get_loaders(
                                       train_records, val_records, 
                                       "cointegrated/rubert-tiny", MAX_TOKENS, 
                                       BATCH_SIZE, NUM_WORKERS,
                                       )


model = ClusteringTripletModel("cointegrated/rubert-tiny", lr=0.0001)
early_stop_callback = EarlyStopping(
    monitor="val_loss",
    min_delta=0.0001,
    patience=3,
    verbose=True,
    mode="min" 
)

checkpoint = ModelCheckpoint(
    monitor='val_loss',
    dirpath='/content/drive/MyDrive/NewsBert/tiny',
    filename='clustering_news_bert_rubert-tiny'
)


trainer = Trainer(
    gpus=1,
    accumulate_grad_batches=ACCUMULATE_GRAD_BATCHES,
    max_epochs=EPOCHS,
    callbacks=[early_stop_callback, checkpoint],
    log_every_n_steps=LOG_EVERY_N_STEPS
)


trainer.fit(model, tiny_train_loader, tiny_val_loader)

In [17]:
torch.save(model.state_dict(), os.path.join('/content/drive/MyDrive/NewsBert/tiny/', f'best-distill-bert.pt'))

In [27]:
model = ClusteringTripletModel.load_from_checkpoint(
    model_path = "cointegrated/rubert-tiny",
    checkpoint_path = '/content/drive/MyDrive/NewsBert/tiny/clustering_news_bert_rubert-tiny.ckpt',
    )

embedder = model.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, embedder, tiny_tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Some weights of the model checkpoint at cointegrated/rubert-tiny were not used when initializing BertModel: ['cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


Mean inference time per embed:  0.6591846915117773 ms

Accuracy: 86.2
Positives Recall: 77.2
Positives Precision: 91.6
Positives F1: 83.8
Distance:  0.38
Max cluster size:  153
Median cluster size:  2.0
Avg cluster size: 2.91


In [28]:
private_distill_embeddings = records_to_embeds(private_set, embedder, tiny_tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.6579545891879242 ms

Accuracy: 85.4
Positives Recall: 75.9
Positives Precision: 90.8
Positives F1: 82.7
Distance:  0.38
Max cluster size:  116
Median cluster size:  2
Avg cluster size: 2.81


In [20]:
BATCH_SIZE = 12

tiny2_train_loader, tiny2_val_loader, tiny2_tokenizer = get_loaders(
                                       train_records, val_records, 
                                       "cointegrated/rubert-tiny2", MAX_TOKENS, 
                                       BATCH_SIZE, NUM_WORKERS,
                                       )

early_stop_callback = EarlyStopping(
    monitor="val_loss",
    min_delta=0.0001,
    patience=3,
    verbose=True,
    mode="min" 
)

model = ClusteringTripletModel("cointegrated/rubert-tiny2", lr=0.0001)

checkpoint = ModelCheckpoint(
    monitor='val_loss',
    dirpath='/content/drive/MyDrive/NewsBert/tiny2',
    filename='clustering_news_bert_rubert-tiny2'
)


trainer = Trainer(
    gpus=1,
    accumulate_grad_batches=ACCUMULATE_GRAD_BATCHES,
    max_epochs=EPOCHS,
    callbacks=[early_stop_callback, checkpoint],
    log_every_n_steps=LOG_EVERY_N_STEPS
)


trainer.fit(model, tiny2_train_loader, tiny2_val_loader)

Downloading:   0%|          | 0.00/401 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.03M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.66M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/112 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/715 [00:00<?, ?B/s]

...

Metric val_loss improved by 0.000 >= min_delta = 0.0001. New best score: 0.005


Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Monitored metric val_loss did not improve in the last 3 records. Best score: 0.005. Signaling Trainer to stop.


In [21]:
torch.save(model.state_dict(), os.path.join('/content/drive/MyDrive/NewsBert/tiny2/', f'best-distill-bert.pt'))

In [29]:
model = ClusteringTripletModel.load_from_checkpoint(
    model_path = "cointegrated/rubert-tiny2",
    checkpoint_path = '/content/drive/MyDrive/NewsBert/tiny2/clustering_news_bert_rubert-tiny2.ckpt',
    )

embedder = model.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, embedder, tiny2_tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Some weights of the model checkpoint at cointegrated/rubert-tiny2 were not used when initializing BertModel: ['cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


Mean inference time per embed:  0.6598458836515586 ms

Accuracy: 91.4
Positives Recall: 86.4
Positives Precision: 94.5
Positives F1: 90.3
Distance:  0.38
Max cluster size:  175
Median cluster size:  2
Avg cluster size: 3.02


In [30]:
private_distill_embeddings = records_to_embeds(private_set, embedder, tiny2_tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.658596769381029 ms

Accuracy: 92.2
Positives Recall: 87.3
Positives Precision: 95.3
Positives F1: 91.1
Distance:  0.38
Max cluster size:  148
Median cluster size:  1
Avg cluster size: 2.92


In [10]:
EPOCHS = 60
BATCH_SIZE = 12
ACCUMULATE_GRAD_BATCHES = 8
LOG_EVERY_N_STEPS = 10


tiny_cased_train_loader, tiny_cased_val_loader, tiny_cased_tokenizer = get_loaders(
                                       train_records, val_records, 
                                       "DeepPavlov/distilrubert-tiny-cased-conversational", 
                                       MAX_TOKENS, 
                                       BATCH_SIZE, NUM_WORKERS,
                                       )


model = ClusteringTripletModel("DeepPavlov/distilrubert-tiny-cased-conversational", lr=0.0001)

early_stop_callback = EarlyStopping(
    monitor="val_loss",
    min_delta=0.0001,
    patience=3,
    verbose=True,
    mode="min" 
)

checkpoint = ModelCheckpoint(
    monitor='val_loss',
    dirpath='/content/drive/MyDrive/NewsBert/tiny_cased',
    filename='clustering_news_bert_rubert-tiny_cased'
)


trainer = Trainer(
    gpus=1,
    accumulate_grad_batches=ACCUMULATE_GRAD_BATCHES,
    max_epochs=EPOCHS,
    callbacks=[early_stop_callback, checkpoint],
    log_every_n_steps=LOG_EVERY_N_STEPS
)


trainer.fit(model, tiny_cased_train_loader, tiny_cased_val_loader)

Some weights of the model checkpoint at DeepPavlov/distilrubert-tiny-cased-conversational were not used when initializing DistilBertModel: ['vocab_layer_norm.weight', 'vocab_projector.weight', 'vocab_layer_norm.bias', 'vocab_transform.bias', 'vocab_projector.bias', 'vocab_transform.weight']
- This IS expected if you are initializing DistilBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
/usr/local/lib/python3.7/dist-packages/transformers/opti

Sanity Checking: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/data_connector.py:245: PossibleUserWarning: The dataloader, val_dataloader 0, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 4 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  category=PossibleUserWarning,
/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/data_connector.py:245: PossibleUserWarning: The dataloader, train_dataloader, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 4 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  category=PossibleUserWarning,


Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

...

Metric val_loss improved by 0.000 >= min_delta = 0.0001. New best score: 0.006


Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Monitored metric val_loss did not improve in the last 3 records. Best score: 0.006. Signaling Trainer to stop.


In [11]:
torch.save(model.state_dict(), os.path.join('/content/drive/MyDrive/NewsBert/tiny_cased/', f'best-distill-bert.pt'))

In [31]:
model = ClusteringTripletModel.load_from_checkpoint(
    model_path = "DeepPavlov/distilrubert-tiny-cased-conversational",
    checkpoint_path = '/content/drive/MyDrive/NewsBert/tiny_cased/clustering_news_bert_rubert-tiny_cased.ckpt',
    )

embedder = model.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, embedder, tiny_cased_tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Some weights of the model checkpoint at DeepPavlov/distilrubert-tiny-cased-conversational were not used when initializing DistilBertModel: ['vocab_projector.bias', 'vocab_layer_norm.bias', 'vocab_projector.weight', 'vocab_transform.bias', 'vocab_transform.weight', 'vocab_layer_norm.weight']
- This IS expected if you are initializing DistilBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


Mean inference time per embed:  1.3636089203367194 ms

Accuracy: 91.5
Positives Recall: 88.9
Positives Precision: 92.5
Positives F1: 90.7
Distance:  0.38
Max cluster size:  234
Median cluster size:  2.0
Avg cluster size: 3.29


In [32]:
private_distill_embeddings = records_to_embeds(private_set, embedder, tiny_cased_tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.3630668045238916 ms

Accuracy: 91.9
Positives Recall: 89.4
Positives Precision: 92.7
Positives F1: 91.0
Distance:  0.38
Max cluster size:  145
Median cluster size:  2
Avg cluster size: 3.20


##--Other embedding architectures--

###Data loading and preprocessing

In [35]:
%cd /content/drive/MyDrive/NewsBert
from initial_finetuned_model import ClusteringTripletModel
from loading_and_evaluation import gen_batch, records_to_embeds, get_quality, NewsDataset, get_loaders

with open('single_full_train_embeddings_bert', 'rb') as pickle_file:
    single_full_train_embeddings_bert = pickle.load(pickle_file)

with open('single_full_val_embeddings_bert', 'rb') as pickle_file:
    single_full_val_embeddings_bert = pickle.load(pickle_file)


with open('full_train_records', 'rb') as pickle_file:
    full_train_records = pickle.load(pickle_file)

with open('full_val_records', 'rb') as pickle_file:
    full_val_records = pickle.load(pickle_file)


with open('public_set', 'rb') as pickle_file:
    public_set = pickle.load(pickle_file)

with open('private_set', 'rb') as pickle_file:
    private_set = pickle.load(pickle_file)


initial_model = ClusteringTripletModel.load_from_checkpoint(
    model_path = INITIAL_MODEL,
    checkpoint_path = '/content/drive/MyDrive/NewsBert/best_clustering_news_bert-val_loss=0.0008.ckpt',
    num_training_steps = None
    )

embedder = initial_model.embedder.cuda()

VOCAB_SIZE = embedder.model.embeddings.word_embeddings.num_embeddings
BATCH_SIZE = 128


public_markup = read_markup_tsv("ru_clustering_0527_urls_final.tsv")
private_markup = read_markup_tsv("ru_clustering_0529_urls_final_v2.tsv")

/content/drive/MyDrive/NewsBert


Some weights of the model checkpoint at IlyaGusev/news_tg_rubert were not used when initializing BertModel: ['cls.predictions.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.bias', 'cls.predictions.decoder.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertModel were not initialized from the model checkpoint at IlyaGusev/news_tg_rubert and are newly initialized: ['bert.pooler.dense.weight', 'bert.pooler.dense.

In [36]:
train_loader, val_loader, tokenizer = get_loaders(full_train_records,
                                                  full_val_records, 
                                                  INITIAL_MODEL, MAX_TOKENS, 
                                                  BATCH_SIZE, 
                                                  single_full_train_embeddings_bert,
                                                  single_full_val_embeddings_bert,
                                                  )                                       

Downloading:   0%|          | 0.00/1.57M [00:00<?, ?B/s]

####Transformer

In [18]:
class TransformerEmbedder(nn.Module):
  def __init__(self, vocab_size=VOCAB_SIZE, 
               target_size=TARGET_SIZE, 
               pretrained=False,  
               pretrained_embs=None,
               freeze_pretrained=False,
               word_emb_dim=56,
               dim_feedforward=1024,
               n_heads=4, 
               n_layers=6,
               relu=False,
               attentive_aggregation=False,
               cls_aggregation=False,
               ):

        super().__init__()
        
        self.target_size=target_size
        self.word_emb_dim=word_emb_dim
        self.relu=relu
        self.attentive_aggregation=attentive_aggregation
        self.cls_aggregation=cls_aggregation
         
        if pretrained:
          self.embedding = nn.Embedding.from_pretrained(pretrained_embs, 
                                                        freeze=freeze_pretrained) 
          word_emb_dim = pretrained_embs.shape[1]
        else:
          self.embedding = nn.Embedding(vocab_size, word_emb_dim)

        self.encoder_layer = nn.TransformerEncoderLayer(word_emb_dim, n_heads,
                                                        dim_feedforward=dim_feedforward, 
                                                        batch_first=True)
        
        self.encoder = nn.TransformerEncoder(self.encoder_layer, n_layers)
        
        if word_emb_dim != target_size:
          self.mapping = nn.Linear(word_emb_dim, target_size)
        
        if cls_aggregation:
          self.cls_pooling_linear = nn.Linear(target_size, target_size)

        if attentive_aggregation:  
          self.softmax = nn.Softmax(dim=1)     
          self.attn = nn.Sequential(
              nn.Linear(target_size, target_size//2),
              nn.ReLU(),
              nn.Linear(target_size//2, 1)
            )
        

        
  def aggregate(self, transformer_output, mask):
        expanded_mask = mask.cuda().unsqueeze(-1).expand(transformer_output.size()).float()
        sum_embeddings = torch.sum(transformer_output * expanded_mask, 1).cuda()
        sum_mask = torch.clamp(expanded_mask.sum(1), min=1e-9)
        return sum_embeddings / sum_mask   

  def cls_aggregate(self, transformer_output):
        cls_emb = nn.functional.relu(self.mapping(transformer_output[:,0,:].squeeze(1)))
        return self.cls_pooling_linear(cls_emb)

  def attentive_aggregate(self, transformer_output, mask):
        weights = self.softmax(self.attn(transformer_output).squeeze(-1)) * mask
        embeddings = weights.unsqueeze(1).bmm(transformer_output).squeeze(1)
        return embeddings 

  def forward(self, x, mask):
        embs = self.embedding(x)
        transformer_output = self.encoder(embs, src_key_padding_mask=mask)
        if self.cls_aggregation:
          out = self.cls_aggregate(transformer_output)
        else:
          if self.word_emb_dim != self.target_size:
            if self.relu:
              transformer_output = self.mapping(nn.functional.relu(transformer_output))
            else:
              transformer_output = self.mapping(transformer_output)
          if self.attentive_aggregation: 
            out = self.attentive_aggregate(transformer_output, mask)
          else:
            out = self.aggregate(transformer_output, mask)
        return out

In [19]:
class TransformerClusteringDistillModel(nn.Module):
    def __init__(self, vocab_size=VOCAB_SIZE, target_size=TARGET_SIZE, 
                 pretrained=False, pretrained_embs=None, 
                 freeze_pretrained=False, word_emb_dim=128, 
                 evaluate_similarity=False, dim_feedforward=1024,
                 lr=1e-3, n_heads=4, n_layers=2, relu=False,
                 attentive_aggregation=False, cls_aggregation=False,
                 ):
      
        super().__init__()

        self.embedder = TransformerEmbedder(vocab_size=vocab_size, 
                                      target_size=target_size, 
                                      pretrained=pretrained,  
                                      pretrained_embs=pretrained_embs,
                                      freeze_pretrained=freeze_pretrained,
                                      word_emb_dim=word_emb_dim,
                                      n_heads=n_heads, 
                                      n_layers=n_layers,
                                      dim_feedforward=dim_feedforward, 
                                      relu=relu,
                                      attentive_aggregation=attentive_aggregation, 
                                      cls_aggregation=cls_aggregation,
                                      )

        self.evaluate_similarity = evaluate_similarity
        if not evaluate_similarity:
          self.mse = torch.nn.MSELoss()
        else:
          self.cosine_similarity = torch.nn.functional.cosine_similarity
        
        self.lr = lr

    def forward(self, news):
        embeddings = self.embedder(news["input_ids"].cuda(), 
                                   news["attention_mask"].cuda())
        return embeddings

    def loss(self, embeds, bert_embeds):
        if self.evaluate_similarity is True:
          similarity = self.cosine_similarity(embeds, bert_embeds)
          loss = torch.mean(torch.ones(len(similarity)).cuda() - similarity)
        else:
          loss = self.mse(embeds.float(), bert_embeds.float())
        return loss

#####1 layer + 4 heads

In [ ]:
transformer_distill_head4_layer1 = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=1,
                                                       )
train(transformer_distill_head4_layer1, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer1',
      )

In [20]:
transformer_distill_head4_layer1 = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=1,
                                                       )

transformer_distill_head4_layer1.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer1/best-distill-bert.pt'))

distill_embedder = transformer_distill_head4_layer1.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.13554358551820436 ms

Accuracy: 91.5
Positives Recall: 91.4
Positives Precision: 90.3
Positives F1: 90.9
Distance:  0.38
Max cluster size:  322
Median cluster size:  2
Avg cluster size: 4.77


In [21]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.13365249270842472 ms

Accuracy: 91.1
Positives Recall: 91.0
Positives Precision: 89.7
Positives F1: 90.4
Distance:  0.38
Max cluster size:  172
Median cluster size:  2
Avg cluster size: 4.58


#####1 layer + 4 heads + relu

In [ ]:
transformer_distill_head4_layer1_relu = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=1,
                                                       relu=True,
                                                       )
train(transformer_distill_head4_layer1_relu, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer1_relu',
      )

In [48]:
transformer_distill_head4_layer1_relu = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=1,
                                                       relu=True,
                                                       )


transformer_distill_head4_layer1_relu.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer1_relu/best-distill-bert.pt'))

distill_embedder = transformer_distill_head4_layer1_relu.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.13353054191605504 ms

Accuracy: 91.5
Positives Recall: 92.0
Positives Precision: 89.8
Positives F1: 90.9
Distance:  0.38
Max cluster size:  310
Median cluster size:  2.0
Avg cluster size: 4.87


In [50]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.13304639458781164 ms

Accuracy: 91.4
Positives Recall: 91.4
Positives Precision: 90.0
Positives F1: 90.7
Distance:  0.38
Max cluster size:  155
Median cluster size:  2.0
Avg cluster size: 4.64


#####1 layer + 4 heads / *attentive aggregation*

In [26]:
transformer_distill_head4_layer1_attn = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=1,
                                                       attentive_aggregation=True)

train(transformer_distill_head4_layer1_attn, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer1_attn',
      )

Train: 100%|██████████| 4037/4037 [05:41<00:00, 11.82it/s]


Train_loss:  0.4259607350616584


Val: 100%|██████████| 1010/1010 [01:19<00:00, 12.73it/s]


Val_loss:  0.3073411729030545


Train: 100%|██████████| 4037/4037 [05:40<00:00, 11.84it/s]


...

Val_loss:  0.16184943478936273


Train: 100%|██████████| 4037/4037 [05:37<00:00, 11.97it/s]


Train_loss:  0.1348120746209958


Val: 100%|██████████| 1010/1010 [01:19<00:00, 12.71it/s]


Val_loss:  0.16046146499656874


In [53]:
transformer_distill_head4_layer1_attn = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=1,
                                                       attentive_aggregation=True)

transformer_distill_head4_layer1_attn.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer1_attn/best-distill-bert.pt'))

distill_embedder = transformer_distill_head4_layer1_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.13569880810035653 ms

Accuracy: 91.8
Positives Recall: 91.8
Positives Precision: 90.6
Positives F1: 91.2
Distance:  0.38
Max cluster size:  306
Median cluster size:  2
Avg cluster size: 4.78


In [54]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.1359656103982254 ms

Accuracy: 91.0
Positives Recall: 91.2
Positives Precision: 89.3
Positives F1: 90.3
Distance:  0.38
Max cluster size:  199
Median cluster size:  2
Avg cluster size: 4.58


#####1 layer + 4 heads / *cls aggregation*

In [23]:
transformer_distill_head4_layer1_cls = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=1,
                                                       cls_aggregation=True)

train(transformer_distill_head4_layer1_cls, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer1_cls',
      )

Train: 100%|██████████| 4037/4037 [05:42<00:00, 11.79it/s]


Train_loss:  0.491431591489802


Val: 100%|██████████| 1010/1010 [01:19<00:00, 12.70it/s]


Val_loss:  0.35244025554346686


Train: 100%|██████████| 4037/4037 [05:38<00:00, 11.92it/s]


...

Val_loss:  0.17801908179671097


Train: 100%|██████████| 4037/4037 [05:33<00:00, 12.09it/s]


Train_loss:  0.17717134800717155


Val: 100%|██████████| 1010/1010 [01:18<00:00, 12.88it/s]


Val_loss:  0.17653300541161046


In [57]:
transformer_distill_head4_layer1_cls = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=1,
                                                       cls_aggregation=True)

transformer_distill_head4_layer1_cls.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer1_cls/best-distill-bert.pt'))

distill_embedder = transformer_distill_head4_layer1_cls.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.12856528292376682 ms

Accuracy: 90.2
Positives Recall: 90.5
Positives Precision: 88.6
Positives F1: 89.5
Distance:  0.38
Max cluster size:  361
Median cluster size:  2
Avg cluster size: 6.11


In [58]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.12428928877039339 ms

Accuracy: 90.1
Positives Recall: 90.5
Positives Precision: 88.2
Positives F1: 89.3
Distance:  0.38
Max cluster size:  190
Median cluster size:  2.0
Avg cluster size: 5.72


In [ ]:
transformer_distill_head4_layer1_cls = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=1,
                                                       cls_aggregation=True)

transformer_distill_head4_layer1_cls.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer1_cls/best-distill-bert.pt'))

#####1 layer + 4 heads + 64 emb dim

In [29]:
transformer_distill_head4_layer1_64 = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=1,
                                                       word_emb_dim=64
                                                       )
train(transformer_distill_head4_layer1_64, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer1_wed64',
      )

Train: 100%|██████████| 4037/4037 [05:29<00:00, 12.24it/s]


Train_loss:  0.5188354424144475


Val: 100%|██████████| 1010/1010 [01:18<00:00, 12.90it/s]


Val_loss:  0.39015187522214795


Train: 100%|██████████| 4037/4037 [05:29<00:00, 12.26it/s]


...

Val_loss:  0.21495729795831836


Train: 100%|██████████| 4037/4037 [05:31<00:00, 12.16it/s]


Train_loss:  0.19491826730805864


Val: 100%|██████████| 1010/1010 [01:19<00:00, 12.69it/s]


Val_loss:  0.21414851585557726


In [39]:
transformer_distill_head4_layer1_64 = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=1,
                                                       word_emb_dim=64)

transformer_distill_head4_layer1_64.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer1_wed64/best-distill-bert.pt'))

distill_embedder = transformer_distill_head4_layer1_64.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.20702503746842957 ms

Accuracy: 90.8
Positives Recall: 90.2
Positives Precision: 89.8
Positives F1: 90.0
Distance:  0.38
Max cluster size:  365
Median cluster size:  2
Avg cluster size: 5.30


In [40]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.19745498281994472 ms

Accuracy: 91.3
Positives Recall: 91.7
Positives Precision: 89.6
Positives F1: 90.6
Distance:  0.38
Max cluster size:  181
Median cluster size:  2
Avg cluster size: 5.08


#####2 layers + 8 heads

In [32]:
transformer_distill_head8_layer2 = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=8,
                                                       n_layers=2,
                                                       )
train(transformer_distill_head8_layer2, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head8_layer2',
      )

Train: 100%|██████████| 4037/4037 [08:31<00:00,  7.89it/s]


Train_loss:  0.42114454950168706


Val: 100%|██████████| 1010/1010 [01:23<00:00, 12.14it/s]


Val_loss:  0.2922313662327121


Train: 100%|██████████| 4037/4037 [08:34<00:00,  7.84it/s]


...

Val_loss:  0.15405414835392742


Train: 100%|██████████| 4037/4037 [08:35<00:00,  7.83it/s]


Train_loss:  0.1268735026272659


Val: 100%|██████████| 1010/1010 [01:22<00:00, 12.22it/s]


Val_loss:  0.15324034990797192


In [59]:
transformer_distill_head8_layer2 = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=8,
                                                       n_layers=2,
                                                       )

transformer_distill_head8_layer2.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head8_layer2/best-distill-bert.pt'))

distill_embedder = transformer_distill_head8_layer2.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.2727834535309993 ms

Accuracy: 91.4
Positives Recall: 91.8
Positives Precision: 89.8
Positives F1: 90.8
Distance:  0.38
Max cluster size:  291
Median cluster size:  2.0
Avg cluster size: 5.44


In [60]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.2726942085800283 ms

Accuracy: 91.3
Positives Recall: 91.2
Positives Precision: 90.0
Positives F1: 90.6
Distance:  0.38
Max cluster size:  225
Median cluster size:  2
Avg cluster size: 5.23


#####1 layer + 8 heads + relu

In [35]:
transformer_distill_head8_layer1_relu = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=8,
                                                       n_layers=1,
                                                       relu=True,
                                                       )
train(transformer_distill_head8_layer1_relu, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head8_layer1_relu',
      )

Train: 100%|██████████| 4037/4037 [05:49<00:00, 11.55it/s]


Train_loss:  0.4650929518486156


Val: 100%|██████████| 1010/1010 [01:20<00:00, 12.56it/s]


Val_loss:  0.3346596614120308


Train: 100%|██████████| 4037/4037 [05:49<00:00, 11.56it/s]


...

Val_loss:  0.16687024167734238


Train: 100%|██████████| 4037/4037 [05:48<00:00, 11.57it/s]


Train_loss:  0.13694441578541755


Val: 100%|██████████| 1010/1010 [01:20<00:00, 12.59it/s]


Val_loss:  0.165658943785824


In [67]:
transformer_distill_head8_layer1_relu = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=8,
                                                       n_layers=1,
                                                       relu=True,                                                      
                                                       )

transformer_distill_head8_layer1_relu.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head8_layer1_relu/best-distill-bert.pt'))

distill_embedder = transformer_distill_head8_layer1_relu.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.15777401268719676 ms

Accuracy: 91.6
Positives Recall: 91.6
Positives Precision: 90.3
Positives F1: 90.9
Distance:  0.38
Max cluster size:  310
Median cluster size:  2.0
Avg cluster size: 4.97


In [68]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.15784077583544914 ms

Accuracy: 91.0
Positives Recall: 91.1
Positives Precision: 89.5
Positives F1: 90.3
Distance:  0.38
Max cluster size:  168
Median cluster size:  2.0
Avg cluster size: 4.84


#####2 layers + 4 heads 

In [13]:
transformer_distill_head4_layer2 = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=2,
                                                       )
train(transformer_distill_head4_layer2, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer2',
      )

Train: 100%|██████████| 4037/4037 [06:08<00:00, 10.95it/s]


Train_loss:  0.42739984548495413


Val: 100%|██████████| 1010/1010 [01:23<00:00, 12.04it/s]


Val_loss:  0.2937647733935266


Train: 100%|██████████| 4037/4037 [06:05<00:00, 11.04it/s]


...

Val_loss:  0.15410583476138154


Train: 100%|██████████| 4037/4037 [06:06<00:00, 11.01it/s]


Train_loss:  0.12636096842735567


Val: 100%|██████████| 1010/1010 [01:23<00:00, 12.11it/s]


Val_loss:  0.15253579891621075


In [14]:
transformer_distill_head4_layer2 = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=2,
                                                       )

transformer_distill_head4_layer2.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer2/best-distill-bert.pt'))

distill_embedder = transformer_distill_head4_layer2.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.22640524771346515 ms

Accuracy: 91.6
Positives Recall: 91.7
Positives Precision: 90.2
Positives F1: 91.0
Distance:  0.38
Max cluster size:  316
Median cluster size:  2.0
Avg cluster size: 5.28


In [15]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.22489633355921765 ms

Accuracy: 90.8
Positives Recall: 90.6
Positives Precision: 89.5
Positives F1: 90.1
Distance:  0.38
Max cluster size:  165
Median cluster size:  2
Avg cluster size: 5.09


#####2 layers + 4 heads / *attentive aggregation*

In [16]:
transformer_distill_head4_layer2_attn = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=2,
                                                       attentive_aggregation=True,
                                                       )
train(transformer_distill_head4_layer2_attn, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer2_attn',
      )

Train: 100%|██████████| 4037/4037 [05:52<00:00, 11.47it/s]


Train_loss:  0.4218944529727063


Val: 100%|██████████| 1010/1010 [01:22<00:00, 12.22it/s]


Val_loss:  0.2920891208366476


Train: 100%|██████████| 4037/4037 [05:55<00:00, 11.36it/s]


...

Val_loss:  0.15465843209999788


Train: 100%|██████████| 4037/4037 [05:54<00:00, 11.40it/s]


Train_loss:  0.12718127146557026


Val: 100%|██████████| 1010/1010 [01:21<00:00, 12.38it/s]


Val_loss:  0.1535096898503754


In [63]:
transformer_distill_head4_layer2_attn = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=2,
                                                       attentive_aggregation=True,
                                                       )

transformer_distill_head4_layer2_attn.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer2_attn/best-distill-bert.pt'))

distill_embedder = transformer_distill_head4_layer2_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.2528980350589372 ms

Accuracy: 91.4
Positives Recall: 91.4
Positives Precision: 90.0
Positives F1: 90.7
Distance:  0.38
Max cluster size:  316
Median cluster size:  2
Avg cluster size: 5.43


In [64]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.22896425135099693 ms

Accuracy: 90.6
Positives Recall: 89.8
Positives Precision: 89.7
Positives F1: 89.7
Distance:  0.38
Max cluster size:  167
Median cluster size:  2
Avg cluster size: 5.18


#####2 layers + 4 heads / *cls aggregation*

In [ ]:
transformer_distill_head4_layer2_cls = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=2,
                                                       cls_aggregation=True,
                                                       )
train(transformer_distill_head4_layer2_cls, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer2_cls',
      )

In [65]:
transformer_distill_head4_layer2_cls = TransformerClusteringDistillModel(evaluate_similarity=True,
                                                       n_heads=4,
                                                       n_layers=2,
                                                       cls_aggregation=True,
                                                       )

transformer_distill_head4_layer2_cls.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Transformer_head4_layer2_cls/best-distill-bert.pt'))

distill_embedder = transformer_distill_head4_layer2_cls.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.21704012896435193 ms

Accuracy: 90.4
Positives Recall: 89.9
Positives Precision: 89.4
Positives F1: 89.6
Distance:  0.38
Max cluster size:  261
Median cluster size:  2.0
Avg cluster size: 5.97


In [66]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.217195659769745 ms

Accuracy: 90.5
Positives Recall: 90.2
Positives Precision: 89.2
Positives F1: 89.7
Distance:  0.38
Max cluster size:  160
Median cluster size:  2.0
Avg cluster size: 5.70


####GRU

#####Zero dropout + deleted linear

In [ ]:
bidir_gru_distill_dropout0_del_linear = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              dropout=0, evaluate_similarity=True,
                              del_linear=True, bidirectional=True,
                              to_gru=True)


train(bidir_gru_distill_dropout0_del_linear, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_GRU_dropout0_del_linear',
      )

In [76]:
bidir_gru_distill_dropout0_del_linear = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              dropout=0, evaluate_similarity=True,
                              del_linear=True, bidirectional=True,
                              to_gru=True)

bidir_gru_distill_dropout0_del_linear.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_GRU_dropout0_del_linear/best-distill-bert.pt'))

distill_embedder = bidir_gru_distill_dropout0_del_linear.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.6163782242759765 ms

Accuracy: 93.8
Positives Recall: 94.5
Positives Precision: 92.3
Positives F1: 93.4
Distance:  0.38
Max cluster size:  269
Median cluster size:  2
Avg cluster size: 3.86


In [77]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.693538889295145 ms

Accuracy: 93.7
Positives Recall: 94.7
Positives Precision: 91.7
Positives F1: 93.2
Distance:  0.38
Max cluster size:  166
Median cluster size:  2.0
Avg cluster size: 3.71


#####Zero dropout + deleted linear + *attentive aggregation*

In [ ]:
bidir_gru_distill_dropout0_del_linear_attn = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              dropout=0, evaluate_similarity=True,
                              del_linear=True, bidirectional=True,
                              to_gru=True, attentive_aggregation=True)


train(bidir_gru_distill_dropout0_del_linear_attn, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_GRU_dropout0_del_linear_attn',
      )

In [85]:
bidir_gru_distill_dropout0_del_linear_attn = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              dropout=0, evaluate_similarity=True,
                              del_linear=True, bidirectional=True,
                              to_gru=True,
                              attentive_aggregation=True)

bidir_gru_distill_dropout0_del_linear_attn.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_GRU_dropout0_del_linear_attn/best-distill-bert.pt'))

distill_embedder = bidir_gru_distill_dropout0_del_linear_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.6399877704234712 ms

Accuracy: 94.1
Positives Recall: 95.1
Positives Precision: 92.4
Positives F1: 93.7
Distance:  0.38
Max cluster size:  260
Median cluster size:  2
Avg cluster size: 3.83


In [86]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.6218457223982505 ms

Accuracy: 93.2
Positives Recall: 94.7
Positives Precision: 90.9
Positives F1: 92.7
Distance:  0.38
Max cluster size:  170
Median cluster size:  2
Avg cluster size: 3.67


#####Zero dropout / GRU with no linear layers

In [ ]:
bidir_gru_distill_dropout0_del_2_linear = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, lstm_hidden_dim=(TARGET_SIZE//2),
                              del_2_linear=True, evaluate_similarity=True,
                              to_gru=True,
                              )

train(bidir_gru_distill_dropout0_del_2_linear, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_GRU_no_linear_0_dropout',
      )

In [79]:
bidir_gru_distill_dropout0_del_2_linear = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, lstm_hidden_dim=(TARGET_SIZE//2),
                              del_2_linear=True, evaluate_similarity=True,
                              to_gru=True,
                              )

bidir_gru_distill_dropout0_del_2_linear.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_GRU_no_linear_0_dropout/best-distill-bert.pt'))

distill_embedder = bidir_gru_distill_dropout0_del_2_linear.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.6090390427060336 ms

Accuracy: 93.7
Positives Recall: 94.4
Positives Precision: 92.2
Positives F1: 93.3
Distance:  0.38
Max cluster size:  253
Median cluster size:  1.0
Avg cluster size: 3.61


In [80]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.6130435019669095 ms

Accuracy: 93.1
Positives Recall: 94.7
Positives Precision: 90.6
Positives F1: 92.6
Distance:  0.38
Max cluster size:  160
Median cluster size:  1
Avg cluster size: 3.47


#####Zero dropout / GRU with no linear layers + *attentive aggregation*

In [ ]:
bidir_gru_distill_dropout0_del_2_linear_attn = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, lstm_hidden_dim=(TARGET_SIZE//2),
                              del_2_linear=True, evaluate_similarity=True,
                              to_gru=True, attentive_aggregation=True,
                              )

train(bidir_gru_distill_dropout0_del_2_linear_attn, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_GRU_no_linear_0_dropout_attn',
      )

In [87]:
bidir_gru_distill_dropout0_del_2_linear_attn = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, lstm_hidden_dim=(TARGET_SIZE//2),
                              del_2_linear=True, evaluate_similarity=True,
                              to_gru=True, attentive_aggregation=True,
                              )

bidir_gru_distill_dropout0_del_2_linear_attn.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_GRU_no_linear_0_dropout_attn/best-distill-bert.pt'))

distill_embedder = bidir_gru_distill_dropout0_del_2_linear_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.6164026565760731 ms

Accuracy: 93.6
Positives Recall: 94.4
Positives Precision: 92.0
Positives F1: 93.2
Distance:  0.38
Max cluster size:  266
Median cluster size:  2.0
Avg cluster size: 3.85


In [88]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.6168262001156657 ms

Accuracy: 93.6
Positives Recall: 95.2
Positives Precision: 91.2
Positives F1: 93.1
Distance:  0.38
Max cluster size:  171
Median cluster size:  2.0
Avg cluster size: 3.68


#####Zero dropout + deleted linear + 2 GRU layers

In [ ]:
bidir_gru_distill_dropout0_del_2gru_layers = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, 
                              del_linear=True, evaluate_similarity=True,
                              lstm_layers_count=2,
                              to_gru=True,
                              )


train(bidir_gru_distill_dropout0_del_2gru_layers, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_GRU_2layers',
      )

In [81]:
bidir_gru_distill_dropout0_del_2gru_layers = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, 
                              del_linear=True, evaluate_similarity=True,
                              lstm_layers_count=2,
                              to_gru=True,)

bidir_gru_distill_dropout0_del_2gru_layers.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_GRU_2layers/best-distill-bert.pt'))

distill_embedder = bidir_gru_distill_dropout0_del_2gru_layers.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.1718134158635993 ms

Accuracy: 93.9
Positives Recall: 94.5
Positives Precision: 92.4
Positives F1: 93.5
Distance:  0.38
Max cluster size:  268
Median cluster size:  2.0
Avg cluster size: 4.05


In [82]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.1707488509666786 ms

Accuracy: 93.9
Positives Recall: 95.3
Positives Precision: 91.7
Positives F1: 93.4
Distance:  0.38
Max cluster size:  169
Median cluster size:  2.0
Avg cluster size: 3.93


#####Zero dropout + deleted linear + 2 GRU layers + *attentive aggregation*

In [ ]:
bidir_gru_distill_dropout0_del_2gru_layers_attn = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, 
                              del_linear=True, evaluate_similarity=True,
                              lstm_layers_count=2,
                              to_gru=True, attentive_aggregation=True,
                              )


train(bidir_gru_distill_dropout0_del_2gru_layers_attn, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_GRU_2layers_attn',
      )

In [89]:
bidir_gru_distill_dropout0_del_2gru_layers_attn = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              bidirectional=True, dropout=0, 
                              del_linear=True, evaluate_similarity=True,
                              lstm_layers_count=2,
                              to_gru=True, attentive_aggregation=True,)

bidir_gru_distill_dropout0_del_2gru_layers_attn.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_GRU_2layers_attn/best-distill-bert.pt'))

distill_embedder = bidir_gru_distill_dropout0_del_2gru_layers_attn.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, 
                                              print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  1.1716535444753577 ms

Accuracy: 94.1
Positives Recall: 95.2
Positives Precision: 92.3
Positives F1: 93.8
Distance:  0.38
Max cluster size:  276
Median cluster size:  2
Avg cluster size: 4.12


In [90]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  1.1355856287714123 ms

Accuracy: 93.5
Positives Recall: 95.0
Positives Precision: 91.2
Positives F1: 93.0
Distance:  0.38
Max cluster size:  167
Median cluster size:  2
Avg cluster size: 3.97


Experiments with other architectures (which haven't shown any competetive results)

###RNN 

In [ ]:
bidir_rnn_distill_dropout0_del_linear = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              add_relu=True, bidirectional=True, evaluate_similarity=True,
                              dropout=0, del_linear=True, to_rnn=True)


train(bidir_rnn_distill_dropout0_del_linear, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_RNN_dropout0_del_linear',
      )

Train: 100%|██████████| 4037/4037 [07:29<00:00,  8.99it/s]


Train_loss:  0.48876522100140124


Val: 100%|██████████| 1010/1010 [01:43<00:00,  9.73it/s]


Val_loss:  0.37218699242468245


Train: 100%|██████████| 4037/4037 [07:20<00:00,  9.16it/s]


...

Val_loss:  0.1809890368405701


Train: 100%|██████████| 4037/4037 [07:07<00:00,  9.45it/s]


Train_loss:  0.147093908937348


Val: 100%|██████████| 1010/1010 [01:37<00:00, 10.33it/s]


Val_loss:  0.18048854259894262


In [ ]:
bidir_rnn_distill_dropout0_del_linear = SingleClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              add_relu=True, bidirectional=True, evaluate_similarity=True,
                              dropout=0, del_linear=True, to_rnn=True)

bidir_rnn_distill_dropout0_del_linear.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/Bidir_RNN_dropout0_del_linear/best-distill-bert.pt'))

distill_embedder = bidir_rnn_distill_dropout0_del_linear.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, max_tokens_count=MAX_TOKENS)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)


Accuracy: 92.0
Positives Recall: 90.8
Positives Precision: 91.8
Positives F1: 91.3
Distance:  0.38
Max cluster size:  253
Median cluster size:  1.0
Avg cluster size: 3.33


In [ ]:
bidir_rnn_distill_dropout0_del_linear.parameters

In [ ]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

###Linears

#####Modeling

In [25]:
class LinearEmbedder(nn.Module):
  def __init__(self, vocab_size=VOCAB_SIZE, 
               target_size=TARGET_SIZE, 
               pretrained=False,  
               pretrained_embs=None,
               freeze_pretrained=False,
               word_emb_dim=64,
               n_layers=3,
               attentive_aggregation=False,
               ):

        super().__init__()
        
        self.target_size=target_size
        self.word_emb_dim=word_emb_dim
        self.attentive_aggregation=attentive_aggregation
         
        if pretrained:
          self.embedding = nn.Embedding.from_pretrained(pretrained_embs, 
                                                        freeze=freeze_pretrained) 
          word_emb_dim = pretrained_embs.shape[1]
        else:
          self.embedding = nn.Embedding(vocab_size, word_emb_dim)

        self.linears = nn.ModuleList()
        for i in range(n_layers):
          linear = nn.Linear(word_emb_dim*(2**i), word_emb_dim*(2**(i+1)))
          self.linears.append(nn.Sequential(linear, 
                                            nn.ReLU()))

        self.mapping = nn.Linear(word_emb_dim*(2**n_layers), target_size)

        if attentive_aggregation: 
          self.softmax = nn.Softmax(dim=1)     
          self.attn = nn.Sequential(
                nn.Linear(target_size, target_size//2),
                nn.ReLU(),
                nn.Linear(target_size//2, 1)
            )
        
        
  def aggregate(self, linears, mask):
        expanded_mask = mask.cuda().unsqueeze(-1).expand(linears.size()).float()
        sum_embeddings = torch.sum(linears * expanded_mask, 1).cuda()
        sum_mask = torch.clamp(expanded_mask.sum(1), min=1e-9)
        return sum_embeddings / sum_mask   

  def attentive_aggregate(self, linears, mask):
        weights = self.softmax(self.attn(linears).squeeze(-1)) * mask
        embeddings = weights.unsqueeze(1).bmm(linears).squeeze(1)
        return embeddings 

  def forward(self, x, mask):
        x = self.embedding(x)
        for layer in self.linears:
          x = layer(x) 
        map = self.mapping(x)
        if self.attentive_aggregation: 
          out = self.attentive_aggregate(map, mask)
        else:
          out = self.aggregate(map, mask)
        return out

In [26]:
class LinearClusteringDistillModel(nn.Module):
    def __init__(self, vocab_size=VOCAB_SIZE, target_size=TARGET_SIZE, 
                 pretrained=False, pretrained_embs=None, 
                 freeze_pretrained=False, word_emb_dim=128, 
                 evaluate_similarity=False, 
                 lr=1e-3, n_layers=3, 
                 attentive_aggregation=False, 
                 ):
      
        super().__init__()

        self.embedder = LinearEmbedder(vocab_size=vocab_size, 
                                      target_size=target_size, 
                                      pretrained=pretrained,  
                                      pretrained_embs=pretrained_embs,
                                      freeze_pretrained=freeze_pretrained,
                                      word_emb_dim=word_emb_dim,
                                      n_layers=n_layers,
                                      attentive_aggregation=attentive_aggregation, 
                                      )

        self.evaluate_similarity = evaluate_similarity
        if not evaluate_similarity:
          self.mse = torch.nn.MSELoss()
        else:
          self.cosine_similarity = torch.nn.functional.cosine_similarity
        
        self.lr = lr

    def forward(self, news):
        embeddings = self.embedder(news["input_ids"].cuda(), 
                                   news["attention_mask"].cuda())
        return embeddings

    def loss(self, embeds, bert_embeds):
        if self.evaluate_similarity is True:
          similarity = self.cosine_similarity(embeds, bert_embeds)
          loss = torch.mean(torch.ones(len(similarity)).cuda() - similarity)
        else:
          loss = self.mse(embeds.float(), bert_embeds.float())
        return loss

#####Experiments

In [49]:
linears_3 = LinearClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              evaluate_similarity=True,
                              )


train(linears_3, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/3_linears',
      )

Train: 100%|██████████| 4037/4037 [05:45<00:00, 11.67it/s]


Train_loss:  0.4071094193074118


Val: 100%|██████████| 1010/1010 [01:21<00:00, 12.33it/s]


Val_loss:  0.26598109546674203


Train: 100%|██████████| 4037/4037 [05:45<00:00, 11.67it/s]


...

Val_loss:  0.18472086073741617


Train: 100%|██████████| 4037/4037 [05:49<00:00, 11.55it/s]


Train_loss:  0.16935822098557732


Val: 100%|██████████| 1010/1010 [01:22<00:00, 12.24it/s]


Val_loss:  0.18386346282518987


In [50]:
linears_3 = LinearClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              evaluate_similarity=True,
                              )

linears_3.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/3_linears/best-distill-bert.pt'))

distill_embedder = linears_3.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.2674005006176542 ms

Accuracy: 91.9
Positives Recall: 91.4
Positives Precision: 91.1
Positives F1: 91.2
Distance:  0.38
Max cluster size:  259
Median cluster size:  2.0
Avg cluster size: 4.16


In [54]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.2701720585121887 ms

Accuracy: 90.3
Positives Recall: 89.8
Positives Precision: 89.2
Positives F1: 89.5
Distance:  0.38
Max cluster size:  145
Median cluster size:  2.0
Avg cluster size: 3.97


In [27]:
linears_2 = LinearClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              evaluate_similarity=True,
                              n_layers=2,
                              )


train(linears_2, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/2_linears',
      )

Train: 100%|██████████| 4037/4037 [05:38<00:00, 11.91it/s]


Train_loss:  0.41829313123727235


Val: 100%|██████████| 1010/1010 [01:21<00:00, 12.41it/s]


Val_loss:  0.32115518810200716


Train: 100%|██████████| 4037/4037 [05:39<00:00, 11.89it/s]


...

Val_loss:  0.2415175290771544


Train: 100%|██████████| 4037/4037 [05:38<00:00, 11.93it/s]


Train_loss:  0.22851532851600412


Val: 100%|██████████| 1010/1010 [01:21<00:00, 12.38it/s]


Val_loss:  0.24032160201970298


In [28]:
linears_2 = LinearClusteringDistillModel(vocab_size = VOCAB_SIZE,
                              evaluate_similarity=True,
                              n_layers=2,
                              )

linears_2.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_Cos_Similarity/2_linears/best-distill-bert.pt'))

distill_embedder = linears_2.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS,  print_mean_timing=True)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

Mean inference time per embed:  0.11830111080966148 ms

Accuracy: 89.0
Positives Recall: 86.6
Positives Precision: 89.3
Positives F1: 87.9
Distance:  0.38
Max cluster size:  350
Median cluster size:  2
Avg cluster size: 4.61


In [29]:
private_distill_embeddings = records_to_embeds(private_set, distill_embedder, tokenizer, batch_size=8, 
                                              max_tokens_count=MAX_TOKENS, print_mean_timing=True)
get_quality(private_markup, private_distill_embeddings, private_set, 0.38, True)

Mean inference time per embed:  0.1184452903516681 ms

Accuracy: 89.0
Positives Recall: 86.8
Positives Precision: 89.0
Positives F1: 87.9
Distance:  0.38
Max cluster size:  151
Median cluster size:  2
Avg cluster size: 4.44


###Convolutions

####Modeling 




In [ ]:
class ConvEmbedder1(nn.Module):
  def __init__(self, vocab_size, target_size=TARGET_SIZE, 
               word_emb_dim=128, seq_len=250,
               pretrained=False, pretrained_embs=None, 
               freeze_pretrained=False,
               ):

        super().__init__()

        if pretrained:
          self.embedding = nn.Embedding.from_pretrained(pretrained_embs, 
                                                        freeze=freeze_pretrained) 
          word_emb_dim = pretrained_embs.shape[1]
        else:
          self.embedding = nn.Embedding(vocab_size, word_emb_dim)

        

        self.model = nn.ModuleList([
          self.embedding,
          nn.Conv2d(1, 3, kernel_size=4, stride=1, padding='same'),
          nn.MaxPool2d(kernel_size=(5, 2)),
          nn.Conv2d(3, 9, kernel_size=3, stride=1, padding='same'),
          nn.MaxPool2d(kernel_size=(5, 2)),
          nn.Conv2d(9, 1, kernel_size=3, stride=1, padding='same'),
          nn.MaxPool2d(kernel_size=((seq_len//25), 1)),
          nn.Linear((word_emb_dim//4), target_size)])        
       
  def forward(self, x):
        for layer in self.model:
          if layer == self.embedding:
            x = torch.unsqueeze(layer(x), 1)
          else:
            x = layer(x)
        return torch.squeeze(x)

In [ ]:
class ConvEmbedder2(nn.Module):
  def __init__(self, vocab_size, target_size=TARGET_SIZE, 
               word_emb_dim=128, seq_len=250,
               pretrained=False, pretrained_embs=None, 
               freeze_pretrained=False,
               ):

        super().__init__()

        if pretrained:
          self.embedding = nn.Embedding.from_pretrained(pretrained_embs, 
                                                        freeze=freeze_pretrained) 
          word_emb_dim = pretrained_embs.shape[1]
        else:
          self.embedding = nn.Embedding(vocab_size, word_emb_dim)

        

        self.model = nn.ModuleList([
          self.embedding,
          nn.Conv2d(1, 3, kernel_size=3, stride=1, padding='same'),
          nn.MaxPool2d(kernel_size=2),
          nn.Conv2d(3, 9, kernel_size=3, stride=1, padding='same'),
          nn.MaxPool2d(kernel_size=2),
          nn.Conv2d(9, 27, kernel_size=2, stride=1, padding='same'),
          nn.MaxPool2d(kernel_size=2),
          nn.Conv2d(27, 81, kernel_size=2, stride=1, padding='same'),
          nn.MaxPool2d(kernel_size=2),
          nn.Conv2d(81, target_size, kernel_size=3, stride=1, padding='same'),
          nn.MaxPool2d(kernel_size=(seq_len//16, word_emb_dim//16))])       
       
  def forward(self, x):
        for layer in self.model:
          if layer == self.embedding:
            x = torch.unsqueeze(layer(x), 1)
          else:
            x = layer(x)
        return torch.squeeze(x)

In [ ]:
class SingleClusteringDistillModelConv(nn.Module):
    def __init__(self, vocab_size, seq_len=250, 
                 target_size=TARGET_SIZE, 
                 word_emb_dim=128, pretrained=False, 
                 pretrained_embs=None, freeze_pretrained=False, 
                 evaluate_similarity=False, lr=1e-3, 
                 conv_embedder_class=ConvEmbedder1,
                 ):
      
        super().__init__()

        self.embedder = conv_embedder_class(vocab_size=vocab_size, target_size=target_size, 
                                      word_emb_dim=word_emb_dim, seq_len=seq_len,
                                      pretrained=pretrained, pretrained_embs=pretrained_embs, 
                                      freeze_pretrained=freeze_pretrained)
        
        self.mse = torch.nn.MSELoss()
        self.evaluate_similarity = evaluate_similarity
        self.cosine_similarity = torch.nn.functional.cosine_similarity
        self.lr = lr


    def forward(self, news):
        if type(news) == dict: 
          embeddings = self.embedder(news["input_ids"].cuda())
        else:
          embeddings = self.embedder(news.cuda())
        return embeddings

    def loss(self, embeds, bert_embeds):
        if self.evaluate_similarity is True:
          similarity = self.cosine_similarity(embeds, bert_embeds)
          loss = torch.mean(torch.ones(len(similarity)).cuda() - similarity)
        else:
          loss = self.mse(embeds.float(), bert_embeds.float())
        return loss

In [ ]:
train_loader, val_loader, tokenizer = get_loaders(full_train_records, full_val_records, 
                                       INITIAL_MODEL, MAX_TOKENS, BATCH_SIZE,
                                       single_full_train_embeddings_bert,
                                       single_full_val_embeddings_bert,
                                       )

Downloading:   0%|          | 0.00/1.57M [00:00<?, ?B/s]

####Experiments

In [ ]:
single_conv_distill = SingleClusteringDistillModelConv(vocab_size = VOCAB_SIZE,
                              seq_len = MAX_TOKENS)


train(single_conv_distill, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_MSE/Conv',
      )

Train:   0%|          | 0/4037 [00:00<?, ?it/s]/usr/local/lib/python3.7/dist-packages/torch/nn/modules/conv.py:443: UserWarning: Using padding='same' with even kernel lengths and odd dilation may require a zero-padded copy of the input be created (Triggered internally at  ../aten/src/ATen/native/Convolution.cpp:647.)
  self.padding, self.dilation, self.groups)
Train: 100%|██████████| 4037/4037 [05:32<00:00, 12.16it/s]


Train_loss:  0.003920611967467619


Val: 100%|██████████| 1010/1010 [01:20<00:00, 12.61it/s]


Val_loss:  0.0037544227258237725


Train: 100%|██████████| 4037/4037 [05:28<00:00, 12.28it/s]


...

Val_loss:  0.0020538690350119875


Train: 100%|██████████| 4037/4037 [05:28<00:00, 12.30it/s]


Train_loss:  0.0019104887229838686


Val: 100%|██████████| 1010/1010 [01:19<00:00, 12.63it/s]


Val_loss:  0.0020512235760089415


In [ ]:
single_conv_distill = SingleClusteringDistillModelConv(vocab_size = VOCAB_SIZE,
                              seq_len = MAX_TOKENS)


single_conv_distill.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_MSE/Conv/best-distill-bert.pt'))

distill_embedder = single_conv_distill.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, max_tokens_count=MAX_TOKENS)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)

TypeError: ignored

In [ ]:
single_conv_distill_002 = SingleClusteringDistillModelConv(vocab_size = VOCAB_SIZE,
                              seq_len = MAX_TOKENS, lr = 1e-2)


train(single_conv_distill_002, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_MSE/Conv_lr001',
      )

Train: 100%|██████████| 4037/4037 [05:24<00:00, 12.45it/s]


Train_loss:  0.0035865528460343804


Val: 100%|██████████| 1010/1010 [01:18<00:00, 12.80it/s]


Val_loss:  0.002607358066079271


Train: 100%|██████████| 4037/4037 [05:23<00:00, 12.49it/s]


...

Val_loss:  0.0019118736519957754


Train: 100%|██████████| 4037/4037 [05:39<00:00, 11.89it/s]


Train_loss:  0.001651831326513914


Val: 100%|██████████| 1010/1010 [01:22<00:00, 12.30it/s]

Val_loss:  0.0019227304311450755


In [ ]:
single_conv_distill = SingleClusteringDistillModelConv(vocab_size = VOCAB_SIZE,
                              seq_len = MAX_TOKENS)


single_conv_distill.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_MSE/Conv_lr001/best-distill-bert.pt'))

distill_embedder = single_conv_distill.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, max_tokens_count=MAX_TOKENS)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)


Accuracy: 90.1
Positives Recall: 85.8
Positives Precision: 92.3
Positives F1: 88.9
Distance:  0.38
Max cluster size:  299
Median cluster size:  3
Avg cluster size: 5.26


In [ ]:
single_conv_distill = SingleClusteringDistillModelConv(vocab_size = VOCAB_SIZE,
                              seq_len = MAX_TOKENS, conv_embedder_class=ConvEmbedder2)


train(single_conv_distill, train_loader, val_loader, 
      20, '/content/drive/MyDrive/NewsBert/Distillation_MSE/Conv2',
      )

Train:   0%|          | 0/4037 [00:00<?, ?it/s]/usr/local/lib/python3.7/dist-packages/torch/nn/modules/conv.py:443: UserWarning: Using padding='same' with even kernel lengths and odd dilation may require a zero-padded copy of the input be created (Triggered internally at  ../aten/src/ATen/native/Convolution.cpp:647.)
  self.padding, self.dilation, self.groups)
Train: 100%|██████████| 4037/4037 [06:53<00:00,  9.77it/s]


Train_loss:  0.003739876204945658


Val: 100%|██████████| 1010/1010 [01:39<00:00, 10.15it/s]


Val_loss:  0.0036125130296712463


Train: 100%|██████████| 4037/4037 [06:54<00:00,  9.75it/s]


...

Val_loss:  0.0020802881504123163


Train: 100%|██████████| 4037/4037 [06:47<00:00,  9.91it/s]


Train_loss:  0.0019341499976602014


Val: 100%|██████████| 1010/1010 [01:34<00:00, 10.71it/s]


Val_loss:  0.002064928708547302


In [ ]:
single_conv_distill = SingleClusteringDistillModelConv(vocab_size = VOCAB_SIZE,
                              seq_len = MAX_TOKENS, conv_embedder_class=ConvEmbedder2)


single_conv_distill.load_state_dict(
    torch.load('/content/drive/MyDrive/NewsBert/Distillation_MSE/Conv2/best-distill-bert.pt'))

distill_embedder = single_conv_distill.embedder.cuda()
public_distill_embeddings = records_to_embeds(public_set, distill_embedder, tokenizer, batch_size=8, max_tokens_count=MAX_TOKENS)
get_quality(public_markup, public_distill_embeddings, public_set, 0.38, True)


Accuracy: 86.7
Positives Recall: 78.5
Positives Precision: 91.5
Positives F1: 84.5
Distance:  0.38
Max cluster size:  283
Median cluster size:  2
Avg cluster size: 4.05
